In [1]:
import os
import numpy as np
from IPython.core.debugger import set_trace
import importlib
import sys
from default_config.masif_opts import masif_opts
from masif_modules.MaSIF_ligand import MaSIF_ligand
from masif_modules.MaSIF_ligand_Brian_tf1 import MaSIF_ligand2
from masif_modules.read_ligand_tfrecords_tf1 import _parse_function
from sklearn.metrics import confusion_matrix
import tensorflow as tf
from default_config.masif_opts import masif_opts


custom_params = {}
custom_params['cache_dir'] = 'nn_models/sc05/cache/'
custom_params['model_dir'] = 'nn_models/sc05/all_feat/model_data/'
custom_params['desc_dir'] = 'output/sc05/all_feat/model_data/'
custom_params['gif_eval_out'] = 'nn_models/sc05/gif_eval/'
custom_params['min_sc_filt'] = 0.5
custom_params['max_sc_filt'] = 1.0
custom_params['pos_surf_accept_probability'] = 1.0

params = masif_opts["site"]
params["n_conv_layers"]=1
for key in custom_params:
    print("Setting {} to {} ".format(key, custom_params[key]))
    params[key] = custom_params[key]


params["max_distance"]=5


2024-08-15 15:51:27.485527: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-08-15 15:51:27.720728: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-08-15 15:51:30.017549: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


Setting cache_dir to nn_models/sc05/cache/ 
Setting model_dir to nn_models/sc05/all_feat/model_data/ 
Setting desc_dir to output/sc05/all_feat/model_data/ 
Setting gif_eval_out to nn_models/sc05/gif_eval/ 
Setting min_sc_filt to 0.5 
Setting max_sc_filt to 1.0 
Setting pos_surf_accept_probability to 1.0 


In [3]:
import glob
ppi_pair_ids=glob.glob("data_preparation/04a-precomputation_12A/precomputation/Sim_1_traj_*")
ppi_pair_ids=[i.split('/')[3] for i in ppi_pair_ids]
len(ppi_pair_ids)

6764

In [17]:
subset

array([   0,    1,    2,    3,    4,    5,    6,    7,    8,    9,   10,
         11,   12,   13,   14,   15,   16,   17,   18,   19,   20,   21,
         22,   23,   24,   25,   26,   27,   28,   29,   30,   31,   32,
         33,   34,   35,   36,   37,   38,   39,   40,   41,   42,   43,
         44,   45,   46,   47,   48,   49,   50,   51,   52,   53,   54,
         55,   56,   57,   58,   59,   60,   61,   62,   63,   64,   65,
         66,   67,   68,   69,   70,   71,   72,   73,   74,   75,   76,
         77,   78,   79,   80,   81,   82,   83,   84,   85,   87,   88,
         89,   90,   91,   92,   93,   94,   95,   96,   97,   98,   99,
        100,  101,  102,  103,  104,  106,  107,  108,  109,  110,  111,
        112,  113,  114,  115,  116,  117,  118,  119,  120,  121,  122,
        123,  124,  125,  126,  127,  128,  129,  130,  131,  132,  133,
        134,  135,  136,  137,  138,  139,  140,  141,  142,  143,  144,
        145,  146,  147,  148,  149,  150,  151,  1

In [57]:
batch_size=200
B=6000
params["n_conv_layers"]=1

ml = []
ml2 = {}

# ppi_pair_id="Sim_1_traj_42_frame_1307"
for i, ppi_pair_id in enumerate(ppi_pair_ids[0:B]):
    try:
        if i % 50 == 0:
            print(i)
        mydir="data_preparation/04a-precomputation_12A/precomputation/" + ppi_pair_id + "/"
        pdbid = ppi_pair_id.split(".")[0]
        pid=pdbid
        rho_wrt_center = np.load(mydir + pid + "_rho_wrt_center.npy")
        theta_wrt_center = np.load(mydir + pid + "_theta_wrt_center.npy")
        input_feat = np.load(mydir + pid + "_input_feat.npy")

        iface_labels = np.load(mydir + pid + "_iface_labels.npy")

        mask = np.load(mydir + pid + "_mask.npy")
        mask = np.expand_dims(mask, 2)
        indices = np.load(mydir + pid + "_list_indices.npy", allow_pickle=True).item()['protein']

        # indices is (n_verts x <30), it should be
        # indices = pad_indices(indices, mask.shape[1])
        tmp = np.zeros((len(iface_labels), 3))
        for i in range(len(iface_labels)):
            if iface_labels[i] == 1:
                tmp[i, 1] = 1
            elif iface_labels[i] == 2:
                tmp[i, 2] = 1
            else:
                tmp[i, 0] = 1
        iface_labels_dc = tmp
        super_pos = np.where(iface_labels == 2)[0]
        pos_labels = np.where(iface_labels == 1)[0]
        neg_labels = np.where(iface_labels == 0)[0]
        # print("PNS",len(pos_labels),len(neg_labels), len(super_pos))


        n = min(len(pos_labels), len(neg_labels))
        # print(ppi_pair_id,"len(pos_labels)", len(pos_labels), 'len(super_pos)', len(super_pos),'len(neg_labels)', len(neg_labels))
        n = min(n, batch_size // 2)
        n_neg = 500-n-len(super_pos)
        # this is 
        subset = np.concatenate([neg_labels[:n_neg], pos_labels[:n], super_pos])
        # print(len(subset))

        rho_wrt_center = rho_wrt_center[subset]
        theta_wrt_center = theta_wrt_center[subset]
        input_feat = input_feat[subset]
        mask = mask[subset]
        iface_labels_dc = iface_labels_dc[subset]
        indices = indices[subset]
        # neg_labels = range(0, (n*5))
        # pos_labels = range((n*5), (n*5)+n)
        # super_pos_labels = range(n+(n*5),n+(n*5)+len(super_pos))
        neg_labels = range(0, n_neg)
        pos_labels = range(n_neg, n_neg+n)
        super_pos_labels = range(n+(n_neg),n+(n_neg)+len(super_pos))
        # print("PNS labels",len(neg_labels),len(pos_labels), len(super_pos_labels))
        # print(ppi_pair_id,"len(pos_labels)", len(pos_labels[:n]), 'len(super_pos_labels)', len(super_pos_labels),'len(neg_labels)', len(neg_labels[:n_neg]), len(np.concatenate([neg_labels,pos_labels,super_pos_labels])))
        assert(len(subset) == 500)

        ml.append([input_feat,rho_wrt_center,theta_wrt_center,mask,iface_labels_dc])
        ml2[ppi_pair_id] = {
            'input_feat':input_feat,
            'rho_wrt_center':rho_wrt_center,
            'theta_wrt_center':theta_wrt_center,
            'mask':mask,
            'iface_labels_dc':iface_labels_dc
        }
    except Exception as e:
        print("Error", e, ppi_pair_id)

np.save("inputs_B%d.npy"%B, ml2)

0
50
100
150
200
250
300
350
400
450
500
550
600
650
700
750
800
850
900
950
1000
1050
1100
1150
1200
1250
1300
1350
1400
1450
1500
1550
1600
1650
1700
1750
1800
1850
1900
1950
2000
2050
2100
2150
2200
2250
2300
2350
2400
2450
2500
2550
2600
2650
2700
2750
2800
2850
2900
2950
3000
3050
3100
3150
3200
3250
3300
3350
3400
3450
3500
3550
3600
3650


In [23]:
if os.path.exists("inputs_B%d.npy"%B):
    print('yes')

yes


In [32]:
len(ml)

500

In [52]:
ml[0][4].shape

(500, 3)

In [53]:
ml=[list(i.values()) for i in list(ml2.values())]

In [24]:
ml2 = np.load("inputs_B%d.npy"%B, allow_pickle=True).item()
# 

{'Sim_1_traj_42_frame_995': {'input_feat': array([[[ 0.33779067,  0.        ,  0.        , -0.04294233,
            0.93333333],
          [ 0.54909056,  0.43821825,  0.        , -0.03106613,
            0.93333333],
          [ 0.99989829,  0.35814391,  0.        , -0.04078233,
            0.93333333],
          ...,
          [ 0.        ,  0.        ,  0.        ,  0.        ,
            0.        ],
          [ 0.        ,  0.        ,  0.        ,  0.        ,
            0.        ],
          [ 0.        ,  0.        ,  0.        ,  0.        ,
            0.        ]],
  
         [[ 0.75497941,  0.        ,  0.        , -0.109466  ,
           -1.        ],
          [ 0.73022871,  0.17690825,  0.        ,  0.09422533,
           -1.        ],
          [ 0.99986124,  0.37557926,  0.        ,  0.18906833,
           -1.        ],
          ...,
          [ 0.        ,  0.        ,  0.        ,  0.        ,
            0.        ],
          [ 0.        ,  0.        ,  0.     

In [13]:
np.save("inputs_B%d.npy"%B, ml2)

In [16]:
6000/B*769/1000

9.228

In [73]:
# import tensorflow as tf
# import tensorflow.keras as keras


# class MyModel(keras.Model):
#   def __init__(self, n_rotations=1):
#     super(MyModel, self).__init__()
#     self.n_rotations=n_rotations,
#     self.conv1 = MaSIF_site2(
#         params["max_distance"],
#         n_thetas=4,
#         n_rhos=3,
#         n_rotations=self.n_rotations,
#         idx_gpu="/gpu:1",
#         feat_mask=[1.0]*5,
#         n_conv_layers=params["n_conv_layers"],
#     )

#   def call(self, inputs):
#     logits = self.conv1(inputs)
#     return logits

In [54]:
TRAIN_TEST_SPLIT = 0.7

class SimDataGenerator():
    """
    Data generator for the UTKFace dataset. This class should be used when training our Keras multi-output model.
    """
    def __init__(self, list_):
        self.list_ = list_
        
    def generate_split_indexes(self):
        p = np.random.permutation(len(self.list_))
        train_up_to = int(len(self.list_) * TRAIN_TEST_SPLIT)
        train_idx = p[:train_up_to]
        test_idx = p[train_up_to:]

        train_up_to = int(train_up_to * TRAIN_TEST_SPLIT)
        train_idx, valid_idx = train_idx[:train_up_to], train_idx[train_up_to:]
        
        # # converts alias to id
        # self.df['gender_id'] = self.df['gender'].map(lambda gender: dataset_dict['gender_alias'][gender])
        # self.df['race_id'] = self.df['race'].map(lambda race: dataset_dict['race_alias'][race])

        # self.max_age = self.df['age'].max()
        
        return train_idx, valid_idx, test_idx

    def generate_frames(self, frame_idx, is_training, batch_size=16):
        """
        Used to generate a batch with images when training/testing/validating our Keras model.
        """
        
        # arrays to store our batched data
        input_feats, rhos, thetas, masks, labels = [], [], [], [], []
        while True:
            for idx in frame_idx:
                sample = self.list_[idx]
                
                input_feat = sample[0]
                rho = sample[1]
                theta = sample[2]
                mask = sample[3]
                label = sample[4]
                
                input_feats.append(input_feat)
                rhos.append(rho)
                thetas.append(theta)
                masks.append(mask)
                labels.append(label)
                
                # yielding condition
                if len(input_feats) >= batch_size:
                    # print("True")
                    yield (np.array(input_feats), np.array(rhos), np.array(thetas), np.array(masks)), np.array(labels)
                    input_feats, rhos, thetas, masks, labels = [], [], [], [], []
                    
            if not is_training:
                break
                
data_generator = SimDataGenerator(ml)
train_idx, valid_idx, test_idx = data_generator.generate_split_indexes()

batch_size = 32
valid_batch_size = 32
train_gen = data_generator.generate_frames(train_idx, is_training=True, batch_size=batch_size)
valid_gen = data_generator.generate_frames(valid_idx, is_training=True, batch_size=valid_batch_size)
test_gen = data_generator.generate_frames(test_idx, is_training=False, batch_size=valid_batch_size)

In [29]:
class MaSIF_site2(tf.keras.layers.Layer):

    def inference(
        self,
        input_feat, # learning_obj.input_feat
        rho_coords, # learning_obj.rho_coords
        theta_coords,
        mask,
        W_conv,
        b_conv,
        mu_rho,
        sigma_rho,
        mu_theta,
        sigma_theta,
        eps=1e-5,
        mean_gauss_activation=True,
    ):
        n_samples = rho_coords.shape[1]
        n_vertices = rho_coords.shape[2]
        # print("n_samples", rho_coords.shape)
        # print("vertices", n_vertices)

        all_conv_feat = []
        for k in range(self.n_rotations):
            # print("rotation", k)
            # print("\trotation", k+1)
            # rho_coords_ = tf.reshape(rho_coords, [-1, 1])  # batch_size*n_vertices
            rho_coords_ = tf.reshape(rho_coords, (-1,n_samples*n_vertices, 1))
            # print("Brian rho_coords,rho_coords_", rho_coords.shape, rho_coords_.shape)
            # thetas_coords_ = tf.reshape(theta_coords, [-1, 1])  # batch_size*n_vertices
            thetas_coords_ = tf.reshape(theta_coords, (-1,n_samples*n_vertices,1))
            # print("thetas_coords,thetas_coords_", theta_coords.shape, thetas_coords_.shape)
            thetas_coords_ += k * 2 * np.pi / self.n_rotations
            thetas_coords_ = tf.math.mod(thetas_coords_, 2 * np.pi)
            rho_coords_ = tf.exp(
                -tf.square(rho_coords_ - mu_rho) / (tf.square(sigma_rho) + eps)
            )
            thetas_coords_ = tf.exp(
                -tf.square(thetas_coords_ - mu_theta) / (tf.square(sigma_theta) + eps)
            )
            
            gauss_activations = tf.multiply(
                rho_coords_, thetas_coords_
            )  # batch_size*n_vertices, n_gauss
            # print("gauss_activations shape 1",gauss_activations.shape)
            # print("gauss_activations1", gauss_activations.shape, rho_coords_.shape, thetas_coords_.shape)
            gauss_activations = tf.reshape(
                # gauss_activations, [n_samples, n_vertices, -1]
                gauss_activations,[-1,n_samples, n_vertices ,tf.shape(gauss_activations)[-1]]
            )  # batch_size, n_vertices, n_gauss
            # print("gauss_activations2", gauss_activations.shape, n_samples, n_vertices,-1)
            # print("gauss_activations shape 2",gauss_activations.shape)
            # print("gauss_activations,mask", gauss_activations.shape, mask.shape)
            gauss_activations = tf.multiply(gauss_activations, mask)
            # print("this is actually working")
            
            if (
                mean_gauss_activation
            ):  # computes mean weights for the different gaussians
                gauss_activations /= (
                    tf.reduce_sum(gauss_activations, 1, keepdims=True) + eps
                )  # batch_size, n_vertices, n_gauss
            # print("1", gauss_activations.shape)
            gauss_activations = tf.expand_dims(
                # gauss_activations, 2
                gauss_activations, 3
            )  # batch_size, inputsize, n_vertices, 1, n_gauss,
            # print("2", gauss_activations.shape)
            input_feat_ = tf.expand_dims(
                # input_feat, 3
                input_feat, 4
            )  # batch_size, inputsize, n_vertices, n_feat, 1
            # print("3", input_feat_.shape)
            gauss_desc = tf.multiply(
                gauss_activations, input_feat_
            )  # batch_size, n_vertices, n_feat, n_gauss,
            # print("4", gauss_desc.shape)
            gauss_desc = tf.reduce_sum(gauss_desc, 2)  # batch_size, n_feat, n_gauss,
            # print("5", gauss_desc.shape)
            gauss_desc = tf.reshape(
                gauss_desc, [-1,n_samples, self.n_thetas * self.n_rhos]
            )  # batch_size, 80
            
            # print("6", gauss_desc.shape)
            conv_feat = tf.matmul(gauss_desc, W_conv) + b_conv  # batch_size, 80
            # print("7", conv_feat.shape)
            # rho_coords2 = tf.identity(conv_feat)
            all_conv_feat.append(conv_feat)

        all_conv_feat = tf.stack(all_conv_feat)
        conv_feat = tf.reduce_max(all_conv_feat, 0)
        conv_feat = tf.nn.relu(conv_feat)
        return conv_feat
        # return 1,2
        
    def __init__(
        self,
        max_rho,
        n_thetas=4,
        n_rhos=3,
        n_gamma=1.0,
        learning_rate=1e-3,
        n_rotations=1,
        idx_gpu="/device:GPU:0",
        feat_mask=[1.0, 1.0, 1.0, 1.0, 1.0],
        n_conv_layers=1,
    ):
        super().__init__()
        self.max_rho=max_rho
       
        self.n_rhos=n_rhos
        self.n_thetas=n_thetas
        self.sigma_rho_init = (
            max_rho / 8
        ) 
        self.sigma_theta_init = 1.0
        self.learning_rate=learning_rate
        self.n_rotations=n_rotations
        self.n_feat = int(sum(feat_mask))
        self.n_labels = 3

        initial_coords = self.compute_initial_coordinates()
        self.initial_coords = initial_coords
        mu_rho_initial = np.expand_dims(initial_coords[:, 0], 0).astype(
                    "float32"
                )
        mu_theta_initial = np.expand_dims(initial_coords[:, 1], 0).astype(
            "float32"
        )
        # print(mu_rho_initial[0:100])
        self.mu_rho = []
        self.mu_theta = []
        self.sigma_rho = []
        self.sigma_theta = []
        for i in range(self.n_feat):
            self.mu_rho.append(
                tf.Variable(mu_rho_initial, name="mu_rho_{}".format(i))
            )  # 1, n_gauss
            self.mu_theta.append(
                tf.Variable(mu_theta_initial, name="mu_theta_{}".format(i))
            )  # 1, n_gauss
            self.sigma_rho.append(
                tf.Variable(
                    np.ones_like(mu_rho_initial) * self.sigma_rho_init,
                    name="sigma_rho_{}".format(i),
                )
            )  # 1, n_gauss
            self.sigma_theta.append(
                tf.Variable(
                    (np.ones_like(mu_theta_initial) * self.sigma_theta_init),
                    name="sigma_theta_{}".format(i),
                )
            )  # 1, n_gauss
        
        
        self.b_conv = []
        for i in range(self.n_feat):
            self.b_conv.append(
                tf.Variable(
                    tf.zeros([self.n_thetas * self.n_rhos]),
                    name="b_conv_{}".format(i),
                )
            )

        self.W_conv = []
        
        for i in range(self.n_feat):
            initializer=tf.keras.initializers.GlorotUniform(seed=(i+1)*100)
            self.W_conv.append(
                    tf.Variable(initializer((self.n_thetas * self.n_rhos, 
                                                self.n_thetas * self.n_rhos)),
                                name="W_conv_{}".format(i)
                                )
            )
        self.mlp2= tf.keras.layers.Dense(
                    self.n_thetas * self.n_rhos,
                    activation=tf.nn.relu,
                )
        self.mlp3= tf.keras.layers.Dense(
                    self.n_feat,
                    activation=tf.nn.relu,
                )
        self.mlp4= tf.keras.layers.Dense(
                    self.n_labels, activation='softmax'
                )
              
        # self.b = self.add_weight(shape=(self.n_ligands*,), initializer="zeros", trainable=True)

    def call(self, inputs):
        # print("INPUTS!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!", len(inputs))
        input_feat=inputs[0]
        print("\tinput_feat", input_feat.shape)
        rho_coords=inputs[1]
        # print("\trho_coords", rho_coords.shape)
        theta_coords=inputs[2]
        # print("\ttheta_coords", theta_coords.shape)
        mask=inputs[3]
        # print("\tmask", mask.shape)
        # self.keep_prob=inputs[4]
        # labels=inputs[5]
    
        self.global_desc_1 = []
        self.rho_coords2 = []
        for i in range(self.n_feat):
        # for i in range(1):
            # print('feature',['si', 'ddc', 'hbond', 'charge', 'hphob'][i])
            # my_input_feat = tf.keras.ops.expand_dims(input_feat[:, :, i], 2)
            my_input_feat = tf.keras.ops.expand_dims(input_feat[:, :, :, i], 3)
            # print("WHAT", my_input_feat.shape)
            conv_feat = self.inference(
                            my_input_feat,
                            rho_coords,
                            theta_coords,
                            mask,
                            self.W_conv[i],
                            self.b_conv[i],
                            self.mu_rho[i],
                            self.sigma_rho[i],
                            self.mu_theta[i],
                            self.sigma_theta[i],
                        )
            self.global_desc_1.append(conv_feat)

        self.global_desc_1 = tf.stack(self.global_desc_1, axis=2)  
        # print("8", self.global_desc_1.shape)

        self.global_desc_1 = tf.reshape(
                    self.global_desc_1, [-1,500, self.n_thetas * self.n_rhos * self.n_feat]
                )
        # print("9", self.global_desc_1.shape)

        self.global_desc_1=self.mlp2(self.global_desc_1)
        # print("10", self.global_desc_1.shape)

        self.global_desc_1=self.mlp3(self.global_desc_1)
        # print("11", self.global_desc_1.shape)
       
        self.logits=self.mlp4(self.global_desc_1)
        # print("shape logits", self.logits.shape)
       
        # return self.global_desc_2, self.logits, self.rho_coords2
        return self.logits


    def compute_initial_coordinates(self):
        range_rho = [0.0, self.max_rho]
        range_theta = [0, 2 * np.pi]

        grid_rho = np.linspace(range_rho[0], range_rho[1], num=self.n_rhos + 1)
        grid_rho = grid_rho[1:]
        grid_theta = np.linspace(range_theta[0], range_theta[1], num=self.n_thetas + 1)
        grid_theta = grid_theta[:-1]

        grid_rho_, grid_theta_ = np.meshgrid(grid_rho, grid_theta, sparse=False)
        grid_rho_ = (
            grid_rho_.T
        )  # the traspose here is needed to have the same behaviour as Matlab code
        grid_theta_ = (
            grid_theta_.T
        )  # the traspose here is needed to have the same behaviour as Matlab code
        grid_rho_ = grid_rho_.flatten()
        grid_theta_ = grid_theta_.flatten()

        coords = np.concatenate((grid_rho_[None, :], grid_theta_[None, :]), axis=0)
        coords = coords.T  # every row contains the coordinates of a grid intersection
        # print(coords.shape)
        return coords

In [30]:
import tensorflow as tf
import tensorflow.keras as keras


class MyModel(keras.Model):
  def __init__(self, n_rotations=1):
    super(MyModel, self).__init__()
    self.n_rotations=n_rotations
    print("self.n_rotations", self.n_rotations)
    self.conv1 = MaSIF_site2(
        params["max_distance"],
        n_thetas=4,
        n_rhos=3,
        n_rotations=self.n_rotations,
        idx_gpu="/gpu:1",
        feat_mask=[1.0]*5,
        n_conv_layers=params["n_conv_layers"],
    )

  def call(self, inputs):
    logits = self.conv1(inputs)
    return logits

# inputA=keras.layers.Input((500,50,5))
# inputB=keras.layers.Input((500,50))
# inputC=keras.layers.Input((500,50))
# inputD=keras.layers.Input((500,50,1))

# model = MyModel(n_rotations=8)
# model([inputA,inputB,inputC,inputD])

In [20]:
len(train_idx)//batch_size

7

In [55]:
# inputA=keras.layers.Input((500,50,5))
# inputB=keras.layers.Input((500,50))
# inputC=keras.layers.Input((500,50))
# inputD=keras.layers.Input((500,50,1))

from keras.callbacks import ModelCheckpoint

model = MyModel(n_rotations=4)
# model([inputA,inputB,inputC,inputD])
callbacks = [
    ModelCheckpoint("./model_checkpoint.keras", monitor='val_loss')
]
model.compile(optimizer=keras.optimizers.Adam(learning_rate= 1e-3), 
    loss='categorical_crossentropy', 
    metrics = ['accuracy'])

model.fit(train_gen, steps_per_epoch=len(train_idx)//batch_size, epochs=5, callbacks=callbacks,
                    validation_data=valid_gen,
                    validation_steps=len(valid_idx)//valid_batch_size)

self.n_rotations 4
Epoch 1/5
	input_feat (None, 500, 50, 5)
	input_feat (None, 500, 50, 5)
	input_feat (None, 500, 50, 5)
	input_feat (None, 500, 50, 5)
7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step - accuracy: 0.7490 - loss: 1.0759	input_feat (None, 500, 50, 5)
7/7 ━━━━━━━━━━━━━━━━━━━━ 29s 1s/step - accuracy: 0.7535 - loss: 1.0749 - val_accuracy: 0.8336 - val_loss: 1.0460
Epoch 2/5
7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 60ms/step - accuracy: 0.8312 - loss: 1.0373 - val_accuracy: 0.8391 - val_loss: 1.0064
Epoch 3/5
7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 56ms/step - accuracy: 0.8372 - loss: 0.9975 - val_accuracy: 0.8365 - val_loss: 0.9678
Epoch 4/5
7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 52ms/step - accuracy: 0.8394 - loss: 0.9578 - val_accuracy: 0.8365 - val_loss: 0.9283
Epoch 5/5
7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 58ms/step - accuracy: 0.8340 - loss: 0.9189 - val_accuracy: 0.8394 - val_loss: 0.8890


In [10]:
# class MaSIF_site2(tf.keras.layers.Layer):

#     def inference(
#         self,
#         input_feat, # learning_obj.input_feat
#         rho_coords, # learning_obj.rho_coords
#         theta_coords,
#         mask,
#         W_conv,
#         b_conv,
#         mu_rho,
#         sigma_rho,
#         mu_theta,
#         sigma_theta,
#         eps=1e-5,
#         mean_gauss_activation=True,
#     ):
#         n_samples = tf.shape(rho_coords)[0]
#         n_vertices = tf.shape(rho_coords)[1]
#         print("n_samples",tf.shape(rho_coords))
#         print("vertices",n_vertices)

#         all_conv_feat = []
#         for k in range(self.n_rotations):
#             # print("\trotation", k+1)
#             rho_coords_ = tf.reshape(rho_coords, [-1, 1])  # batch_size*n_vertices
#             # rho_coords_ = tf.reshape(rho_coords, (-1,500*50, 1))
#             print("Brian rho_coords,rho_coords_", rho_coords.shape, rho_coords_.shape)
#             thetas_coords_ = tf.reshape(theta_coords, [-1, 1])  # batch_size*n_vertices
#             # thetas_coords_ = tf.reshape(theta_coords, (-1,500*50,1))
#             print("thetas_coords,thetas_coords_", theta_coords.shape, thetas_coords_.shape)
#             thetas_coords_ += k * 2 * np.pi / self.n_rotations
#             thetas_coords_ = tf.math.mod(thetas_coords_, 2 * np.pi)
#             rho_coords_ = tf.exp(
#                 -tf.square(rho_coords_ - mu_rho) / (tf.square(sigma_rho) + eps)
#             )
#             thetas_coords_ = tf.exp(
#                 -tf.square(thetas_coords_ - mu_theta) / (tf.square(sigma_theta) + eps)
#             )
            
#             gauss_activations = tf.multiply(
#                 rho_coords_, thetas_coords_
#             )  # batch_size*n_vertices, n_gauss
#             # print("gauss_activations shape 1",gauss_activations.shape)
#             print("gauss_activations1", gauss_activations.shape, rho_coords_.shape, thetas_coords_.shape)
#             gauss_activations = tf.reshape(
#                 gauss_activations, [n_samples, n_vertices, -1]
#                 # gauss_activations,[-1,500, 50,tf.shape(gauss_activations)[-1]]
#             )  # batch_size, n_vertices, n_gauss
#             # print("gauss_activations2", gauss_activations.shape, n_samples, n_vertices,-1)
#             # print("gauss_activations shape 2",gauss_activations.shape)
#             print("gauss_activations,mask", gauss_activations.shape, mask.shape)
#             gauss_activations = tf.multiply(gauss_activations, mask)
#             print("this is actually working")
            
#             if (
#                 mean_gauss_activation
#             ):  # computes mean weights for the different gaussians
#                 gauss_activations /= (
#                     tf.reduce_sum(gauss_activations, 1, keepdims=True) + eps
#                 )  # batch_size, n_vertices, n_gauss
#             print("1", gauss_activations.shape)
#             gauss_activations = tf.expand_dims(
#                 gauss_activations, 2
#                 # gauss_activations, 3
#             )  # batch_size, inputsize, n_vertices, 1, n_gauss,
#             print("2", gauss_activations.shape)
#             input_feat_ = tf.expand_dims(
#                 input_feat, 3
#                 # input_feat, 4
#             )  # batch_size, inputsize, n_vertices, n_feat, 1
#             print("3", input_feat_.shape)
#             gauss_desc = tf.multiply(
#                 gauss_activations, input_feat_
#             )  # batch_size, n_vertices, n_feat, n_gauss,
#             print("4", gauss_desc.shape)
#             gauss_desc = tf.reduce_sum(gauss_desc, 1)  # batch_size, n_feat, n_gauss,
#             print("5", gauss_desc.shape)
#             gauss_desc = tf.reshape(
#                 gauss_desc, [n_samples, self.n_thetas * self.n_rhos]
#             )  # batch_size, 80
            
#             print("6", gauss_desc.shape)
#             conv_feat = tf.matmul(gauss_desc, W_conv) + b_conv  # batch_size, 80
#             print("7", conv_feat.shape)
#             rho_coords2 = tf.identity(conv_feat)
#             all_conv_feat.append(conv_feat)

#         all_conv_feat = tf.stack(all_conv_feat)
#         conv_feat = tf.reduce_max(all_conv_feat, 0)
#         conv_feat = tf.nn.relu(conv_feat)
#         return conv_feat, rho_coords2
#         # return 1,2
        
#     def __init__(
#         self,
#         max_rho,
#         n_thetas=4,
#         n_rhos=3,
#         n_gamma=1.0,
#         learning_rate=1e-3,
#         n_rotations=1,
#         idx_gpu="/device:GPU:0",
#         feat_mask=[1.0, 1.0, 1.0, 1.0, 1.0],
#         n_conv_layers=1,
#     ):
#         super().__init__()
#         self.max_rho=max_rho
       
#         self.n_rhos=n_rhos
#         self.n_thetas=n_thetas
#         self.sigma_rho_init = (
#             max_rho / 8
#         ) 
#         self.sigma_theta_init = 1.0
#         self.learning_rate=learning_rate
#         self.n_rotations=n_rotations
#         self.n_feat = int(sum(feat_mask))
#         self.n_labels = 3

#         initial_coords = self.compute_initial_coordinates()
#         self.initial_coords = initial_coords
#         mu_rho_initial = np.expand_dims(initial_coords[:, 0], 0).astype(
#                     "float32"
#                 )
#         mu_theta_initial = np.expand_dims(initial_coords[:, 1], 0).astype(
#             "float32"
#         )
#         # print(mu_rho_initial[0:100])
#         self.mu_rho = []
#         self.mu_theta = []
#         self.sigma_rho = []
#         self.sigma_theta = []
#         for i in range(self.n_feat):
#             self.mu_rho.append(
#                 tf.Variable(mu_rho_initial, name="mu_rho_{}".format(i))
#             )  # 1, n_gauss
#             self.mu_theta.append(
#                 tf.Variable(mu_theta_initial, name="mu_theta_{}".format(i))
#             )  # 1, n_gauss
#             self.sigma_rho.append(
#                 tf.Variable(
#                     np.ones_like(mu_rho_initial) * self.sigma_rho_init,
#                     name="sigma_rho_{}".format(i),
#                 )
#             )  # 1, n_gauss
#             self.sigma_theta.append(
#                 tf.Variable(
#                     (np.ones_like(mu_theta_initial) * self.sigma_theta_init),
#                     name="sigma_theta_{}".format(i),
#                 )
#             )  # 1, n_gauss
        
        
#         self.b_conv = []
#         for i in range(self.n_feat):
#             self.b_conv.append(
#                 tf.Variable(
#                     tf.zeros([self.n_thetas * self.n_rhos]),
#                     name="b_conv_{}".format(i),
#                 )
#             )

#         self.W_conv = []
#         initializer=tf.keras.initializers.glorot_normal(seed=0)
#         for i in range(self.n_feat):
#             self.W_conv.append(
#                     tf.Variable(glorot_uniform((self.n_thetas * self.n_rhos, 
#                                                 self.n_thetas * self.n_rhos),
#                                             seed=(i+1)*100),
#                                 name="W_conv_{}".format(i)
#                                 )
#             )
#         self.mlp2= tf.keras.layers.Dense(
#                     self.n_thetas * self.n_rhos,
#                     activation=tf.nn.relu,
#                 )
#         self.mlp3= tf.keras.layers.Dense(
#                     self.n_feat,
#                     activation=tf.nn.relu,
#                 )
#         self.mlp4= tf.keras.layers.Dense(
#                     self.n_labels, activation='softmax'
#                 )
              
#         # self.b = self.add_weight(shape=(self.n_ligands*,), initializer="zeros", trainable=True)

#     def call(self, inputs):
#         print("INPUTS!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!", len(inputs))
#         input_feat=inputs[0]
#         print("\tinput_feat", input_feat.shape)
#         rho_coords=inputs[1]
#         print("\trho_coords", rho_coords.shape)
#         theta_coords=inputs[2]
#         print("\ttheta_coords", theta_coords.shape)
#         mask=inputs[3]
#         print("\tmask", mask.shape)
#         # self.keep_prob=inputs[4]
#         # labels=inputs[5]
    
#         self.global_desc_1 = []
#         self.rho_coords2 = []
#         for i in range(self.n_feat):
#         # for i in range(1):
#             # print('feature',['si', 'ddc', 'hbond', 'charge', 'hphob'][i])
#             my_input_feat = tf.keras.ops.expand_dims(input_feat[:, :, i], 2)
#             # my_input_feat = tf.keras.ops.expand_dims(input_feat[:, :, :, i], 3)
#             print("WHAT", my_input_feat.shape)
#             conv_feat, rho_coords2, = self.inference(
#                             my_input_feat,
#                             rho_coords,
#                             theta_coords,
#                             mask,
#                             self.W_conv[i],
#                             self.b_conv[i],
#                             self.mu_rho[i],
#                             self.sigma_rho[i],
#                             self.mu_theta[i],
#                             self.sigma_theta[i],
#                         )
#             self.global_desc_1.append(conv_feat)
            

#         self.global_desc_1 = tf.stack(self.global_desc_1, axis=1)
#         print("8", self.global_desc_1.shape)
#         self.global_desc_1 = tf.reshape(
#                     self.global_desc_1, [-1, self.n_thetas * self.n_rhos * self.n_feat]
#                 )
#         print("9", self.global_desc_1.shape)
#         self.global_desc_1=self.mlp2(self.global_desc_1)
#         # self.global_desc_1 = tf.keras.layers.Dense(
#         #             self.n_thetas * self.n_rhos,
#         #             activation=tf.nn.relu,
#         #         )(self.global_desc_1)
#         print("10", self.global_desc_1.shape)
#         self.global_desc_1=self.mlp3(self.global_desc_1)
#         print("11", self.global_desc_1.shape)
#         # self.global_desc_1 = tf.keras.layers.Dense(
#         #             self.n_feat, activation=tf.nn.relu
#         #         )(self.global_desc_1)
#         self.logits=self.mlp4(self.global_desc_1)
#         print("shape logits", self.logits.shape)
#         # self.logits = tf.keras.layers.Dense(
#         #             self.n_labels, activation='softmax'
#         # )(self.global_desc_1)
        
#         # return self.global_desc_2, self.logits, self.rho_coords2
#         return self.logits

    
#     def compute_initial_coordinates(self):
#         range_rho = [0.0, self.max_rho]
#         range_theta = [0, 2 * np.pi]

#         grid_rho = np.linspace(range_rho[0], range_rho[1], num=self.n_rhos + 1)
#         grid_rho = grid_rho[1:]
#         grid_theta = np.linspace(range_theta[0], range_theta[1], num=self.n_thetas + 1)
#         grid_theta = grid_theta[:-1]

#         grid_rho_, grid_theta_ = np.meshgrid(grid_rho, grid_theta, sparse=False)
#         grid_rho_ = (
#             grid_rho_.T
#         )  # the traspose here is needed to have the same behaviour as Matlab code
#         grid_theta_ = (
#             grid_theta_.T
#         )  # the traspose here is needed to have the same behaviour as Matlab code
#         grid_rho_ = grid_rho_.flatten()
#         grid_theta_ = grid_theta_.flatten()

#         coords = np.concatenate((grid_rho_[None, :], grid_theta_[None, :]), axis=0)
#         coords = coords.T  # every row contains the coordinates of a grid intersection
#         print(coords.shape)
#         return coords

# model = MyModel()
# logits = model([input_feat,rho,theta,mask])

NameError: name 'MyModel' is not defined

In [22]:
test_gen = data_generator.generate_frames(test_idx, is_training=False, batch_size=valid_batch_size)

model.evaluate(test_gen, steps=len(test_idx)//valid_batch_size, 
               callbacks=callbacks)


4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - accuracy: 0.8370 - loss: 0.9592


[0.9591756463050842, 0.8375000357627869]

In [ ]:
class MaSIF_site2(tf.keras.layers.Layer):

    def inference(
        self,
        input_feat, # learning_obj.input_feat
        rho_coords, # learning_obj.rho_coords
        theta_coords,
        mask,
        W_conv,
        b_conv,
        mu_rho,
        sigma_rho,
        mu_theta,
        sigma_theta,
        eps=1e-5,
        mean_gauss_activation=True,
    ):
        n_samples = rho_coords.shape[1]
        n_vertices = rho_coords.shape[2]
        # print("n_samples", rho_coords.shape)
        # print("vertices", n_vertices)

        all_conv_feat = []
        for k in range(self.n_rotations):
            print("rotation", k)
            # print("\trotation", k+1)
            # rho_coords_ = tf.reshape(rho_coords, [-1, 1])  # batch_size*n_vertices
            rho_coords_ = tf.reshape(rho_coords, (-1,n_samples*n_vertices, 1))
            # print("Brian rho_coords,rho_coords_", rho_coords.shape, rho_coords_.shape)
            # thetas_coords_ = tf.reshape(theta_coords, [-1, 1])  # batch_size*n_vertices
            thetas_coords_ = tf.reshape(theta_coords, (-1,n_samples*n_vertices,1))
            # print("thetas_coords,thetas_coords_", theta_coords.shape, thetas_coords_.shape)
            thetas_coords_ += k * 2 * np.pi / self.n_rotations
            thetas_coords_ = tf.math.mod(thetas_coords_, 2 * np.pi)
            rho_coords_ = tf.exp(
                -tf.square(rho_coords_ - mu_rho) / (tf.square(sigma_rho) + eps)
            )
            thetas_coords_ = tf.exp(
                -tf.square(thetas_coords_ - mu_theta) / (tf.square(sigma_theta) + eps)
            )
            
            gauss_activations = tf.multiply(
                rho_coords_, thetas_coords_
            )  # batch_size*n_vertices, n_gauss
            # print("gauss_activations shape 1",gauss_activations.shape)
            # print("gauss_activations1", gauss_activations.shape, rho_coords_.shape, thetas_coords_.shape)
            gauss_activations = tf.reshape(
                # gauss_activations, [n_samples, n_vertices, -1]
                gauss_activations,[-1,n_samples, n_vertices ,tf.shape(gauss_activations)[-1]]
            )  # batch_size, n_vertices, n_gauss
            # print("gauss_activations2", gauss_activations.shape, n_samples, n_vertices,-1)
            # print("gauss_activations shape 2",gauss_activations.shape)
            # print("gauss_activations,mask", gauss_activations.shape, mask.shape)
            gauss_activations = tf.multiply(gauss_activations, mask)
            # print("this is actually working")
            
            if (
                mean_gauss_activation
            ):  # computes mean weights for the different gaussians
                gauss_activations /= (
                    tf.reduce_sum(gauss_activations, 1, keepdims=True) + eps
                )  # batch_size, n_vertices, n_gauss
            # print("1", gauss_activations.shape)
            gauss_activations = tf.expand_dims(
                # gauss_activations, 2
                gauss_activations, 3
            )  # batch_size, inputsize, n_vertices, 1, n_gauss,
            # print("2", gauss_activations.shape)
            input_feat_ = tf.expand_dims(
                # input_feat, 3
                input_feat, 4
            )  # batch_size, inputsize, n_vertices, n_feat, 1
            # print("3", input_feat_.shape)
            gauss_desc = tf.multiply(
                gauss_activations, input_feat_
            )  # batch_size, n_vertices, n_feat, n_gauss,
            # print("4", gauss_desc.shape)
            gauss_desc = tf.reduce_sum(gauss_desc, 2)  # batch_size, n_feat, n_gauss,
            # print("5", gauss_desc.shape)
            gauss_desc = tf.reshape(
                gauss_desc, [-1,n_samples, self.n_thetas * self.n_rhos]
            )  # batch_size, 80
            
            # print("6", gauss_desc.shape)
            conv_feat = tf.matmul(gauss_desc, W_conv) + b_conv  # batch_size, 80
            print("7", conv_feat.shape)
            # rho_coords2 = tf.identity(conv_feat)
            all_conv_feat.append(conv_feat)

        all_conv_feat = tf.stack(all_conv_feat)
        conv_feat = tf.reduce_max(all_conv_feat, 0)
        conv_feat = tf.nn.relu(conv_feat)
        return conv_feat
        # return 1,2
        
    def __init__(
        self,
        max_rho,
        n_thetas=4,
        n_rhos=3,
        n_gamma=1.0,
        learning_rate=1e-3,
        n_rotations=1,
        idx_gpu="/device:GPU:0",
        feat_mask=[1.0, 1.0, 1.0, 1.0, 1.0],
        n_conv_layers=1,
    ):
        super().__init__()
        self.max_rho=max_rho
       
        self.n_rhos=n_rhos
        self.n_thetas=n_thetas
        self.sigma_rho_init = (
            max_rho / 8
        ) 
        self.sigma_theta_init = 1.0
        self.learning_rate=learning_rate
        self.n_rotations=n_rotations
        self.n_feat = int(sum(feat_mask))
        self.n_labels = 3

        initial_coords = self.compute_initial_coordinates()
        self.initial_coords = initial_coords
        mu_rho_initial = np.expand_dims(initial_coords[:, 0], 0).astype(
                    "float32"
                )
        mu_theta_initial = np.expand_dims(initial_coords[:, 1], 0).astype(
            "float32"
        )
        # print(mu_rho_initial[0:100])
        self.mu_rho = []
        self.mu_theta = []
        self.sigma_rho = []
        self.sigma_theta = []
        for i in range(self.n_feat):
            self.mu_rho.append(
                tf.Variable(mu_rho_initial, name="mu_rho_{}".format(i))
            )  # 1, n_gauss
            self.mu_theta.append(
                tf.Variable(mu_theta_initial, name="mu_theta_{}".format(i))
            )  # 1, n_gauss
            self.sigma_rho.append(
                tf.Variable(
                    np.ones_like(mu_rho_initial) * self.sigma_rho_init,
                    name="sigma_rho_{}".format(i),
                )
            )  # 1, n_gauss
            self.sigma_theta.append(
                tf.Variable(
                    (np.ones_like(mu_theta_initial) * self.sigma_theta_init),
                    name="sigma_theta_{}".format(i),
                )
            )  # 1, n_gauss
        
        
        self.b_conv = []
        for i in range(self.n_feat):
            self.b_conv.append(
                tf.Variable(
                    tf.zeros([self.n_thetas * self.n_rhos]),
                    name="b_conv_{}".format(i),
                )
            )

        self.W_conv = []
        
        for i in range(self.n_feat):
            initializer=tf.keras.initializers.GlorotUniform(seed=(i+1)*100)
            self.W_conv.append(
                    tf.Variable(initializer((self.n_thetas * self.n_rhos, 
                                                self.n_thetas * self.n_rhos)),
                                name="W_conv_{}".format(i)
                                )
            )
        self.mlp2= tf.keras.layers.Dense(
                    self.n_thetas * self.n_rhos,
                    activation=tf.nn.relu,
                )
        self.mlp3= tf.keras.layers.Dense(
                    self.n_feat,
                    activation=tf.nn.relu,
                )
        self.mlp4= tf.keras.layers.Dense(
                    self.n_labels, activation='softmax'
                )
              
        # self.b = self.add_weight(shape=(self.n_ligands*,), initializer="zeros", trainable=True)

    def call(self, inputs):
        # print("INPUTS!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!", len(inputs))
        input_feat=inputs[0]
        print("\tinput_feat", input_feat.shape)
        rho_coords=inputs[1]
        # print("\trho_coords", rho_coords.shape)
        theta_coords=inputs[2]
        # print("\ttheta_coords", theta_coords.shape)
        mask=inputs[3]
        # print("\tmask", mask.shape)
        # self.keep_prob=inputs[4]
        # labels=inputs[5]
    
        self.global_desc_1 = []
        self.rho_coords2 = []
        for i in range(self.n_feat):
        # for i in range(1):
            print('feature',['si', 'ddc', 'hbond', 'charge', 'hphob'][i])
            # my_input_feat = tf.keras.ops.expand_dims(input_feat[:, :, i], 2)
            my_input_feat = tf.keras.ops.expand_dims(input_feat[:, :, :, i], 3)
            # print("WHAT", my_input_feat.shape)
            conv_feat = self.inference(
                            my_input_feat,
                            rho_coords,
                            theta_coords,
                            mask,
                            self.W_conv[i],
                            self.b_conv[i],
                            self.mu_rho[i],
                            self.sigma_rho[i],
                            self.mu_theta[i],
                            self.sigma_theta[i],
                        )
            self.global_desc_1.append(conv_feat)

        self.global_desc_1 = tf.stack(self.global_desc_1, axis=2)  
        # print("8", self.global_desc_1.shape)

        self.global_desc_1 = tf.reshape(
                    self.global_desc_1, [-1,500, self.n_thetas * self.n_rhos * self.n_feat]
                )
        # print("9", self.global_desc_1.shape)

        self.global_desc_1=self.mlp2(self.global_desc_1)
        # print("10", self.global_desc_1.shape)

        self.global_desc_1=self.mlp3(self.global_desc_1)
        # print("11", self.global_desc_1.shape)
       
        self.logits=self.mlp4(self.global_desc_1)
        print("shape logits", self.logits.shape)
       
        # return self.global_desc_2, self.logits, self.rho_coords2
        return self.logits


    def compute_initial_coordinates(self):
        range_rho = [0.0, self.max_rho]
        range_theta = [0, 2 * np.pi]

        grid_rho = np.linspace(range_rho[0], range_rho[1], num=self.n_rhos + 1)
        grid_rho = grid_rho[1:]
        grid_theta = np.linspace(range_theta[0], range_theta[1], num=self.n_thetas + 1)
        grid_theta = grid_theta[:-1]

        grid_rho_, grid_theta_ = np.meshgrid(grid_rho, grid_theta, sparse=False)
        grid_rho_ = (
            grid_rho_.T
        )  # the traspose here is needed to have the same behaviour as Matlab code
        grid_theta_ = (
            grid_theta_.T
        )  # the traspose here is needed to have the same behaviour as Matlab code
        grid_rho_ = grid_rho_.flatten()
        grid_theta_ = grid_theta_.flatten()

        coords = np.concatenate((grid_rho_[None, :], grid_theta_[None, :]), axis=0)
        coords = coords.T  # every row contains the coordinates of a grid intersection
        # print(coords.shape)
        return coords



In [366]:
import tensorflow as tf
import tensorflow.keras as keras


class MyModel(keras.Model):
  def __init__(self):
    super(MyModel, self).__init__()
    self.conv1 = MaSIF_site2(
        params["max_distance"],
        n_thetas=4,
        n_rhos=3,
        n_rotations=1,
        idx_gpu="/gpu:1",
        feat_mask=[1.0]*5,
        n_conv_layers=params["n_conv_layers"],
    )

  def call(self, inputs):
    logits = self.conv1(inputs)
    return logits

In [42]:
def glorot_uniform(shape, seed=None):
    if seed is not None:
        np.random.seed(seed)
    limit = np.sqrt(6 / (shape[0] + shape[1]))
    return np.random.uniform(-limit, limit, size=shape).astype(np.float32)

In [152]:
class MaSIF_ligand2(tf.keras.layers.Layer):
    def __init__(
        self,
        max_rho,
        n_ligands,
        n_thetas=16,
        n_rhos=5,
        n_gamma=1.0,
        learning_rate=1e-4,
        n_rotations=16,
        idx_gpu="/gpu:0",
        feat_mask=[1.0, 1.0, 1.0, 1.0],
        costfun="dprime"
    ):
        super().__init__()
        self.max_rho=max_rho
        self.n_ligands=n_ligands
        self.n_rhos=n_rhos
        self.n_thetas=n_thetas
        self.sigma_rho_init = (
            max_rho / 8
        ) 
        self.sigma_theta_init = 1.0
        self.learning_rate=learning_rate
        self.n_rotations=n_rotations
        self.n_feat = int(sum(feat_mask))

        initial_coords = self.compute_initial_coordinates()
        mu_rho_initial = np.expand_dims(initial_coords[:, 0], 0).astype(
                    "float32"
                )
        mu_theta_initial = np.expand_dims(initial_coords[:, 1], 0).astype(
            "float32"
        )
        print(mu_rho_initial[0:100])
        self.mu_rho = []
        self.mu_theta = []
        self.sigma_rho = []
        self.sigma_theta = []
        for i in range(self.n_feat):
            self.mu_rho.append(
                tf.Variable(mu_rho_initial, name="mu_rho_{}".format(i))
            )  # 1, n_gauss
            self.mu_theta.append(
                tf.Variable(mu_theta_initial, name="mu_theta_{}".format(i))
            )  # 1, n_gauss
            self.sigma_rho.append(
                tf.Variable(
                    np.ones_like(mu_rho_initial) * self.sigma_rho_init,
                    name="sigma_rho_{}".format(i),
                )
            )  # 1, n_gauss
            self.sigma_theta.append(
                tf.Variable(
                    (np.ones_like(mu_theta_initial) * self.sigma_theta_init),
                    name="sigma_theta_{}".format(i),
                )
            )  # 1, n_gauss
        
        
        self.b_conv = []
        for i in range(self.n_feat):
            self.b_conv.append(
                tf.Variable(
                    tf.zeros([self.n_thetas * self.n_rhos]),
                    name="b_conv_{}".format(i),
                )
            )

        self.W_conv = []
        initializer=tf.keras.initializers.glorot_normal(seed=0)
        for i in range(self.n_feat):
            self.W_conv.append(
                    tf.Variable(glorot_uniform((80, 80), seed=(i+1)*100),
                                name="W_conv_{}".format(i)
                                )
            )
        # self.b = self.add_weight(shape=(self.n_ligands*,), initializer="zeros", trainable=True)

    def call(self, inputs):
        input_feat=inputs[0]
        rho_coords=inputs[1]
        theta_coords=inputs[2]
        mask=inputs[3]
        labels=inputs[4]
        self.keep_prob=inputs[5]
    
        self.global_desc_1 = []
        self.rho_coords2 = []
        for i in range(self.n_feat):
            print('feature',['si', 'ddc', 'hbond', 'charge', 'hphob'][i])
            my_input_feat = tf.keras.ops.expand_dims(input_feat[:, :, i], 2)
            conv_feat, rho_coords2, = self.inference(
                            my_input_feat,
                            rho_coords,
                            theta_coords,
                            mask,
                            self.W_conv[i],
                            self.b_conv[i],
                            self.mu_rho[i],
                            self.sigma_rho[i],
                            self.mu_theta[i],
                            self.sigma_theta[i],
                            
                        )
            self.global_desc_1.append(conv_feat)
            self.rho_coords2.append(rho_coords2)

        self.global_desc_1 = tf.stack(self.global_desc_1, axis=1)
        self.global_desc_1 = tf.reshape(
                    self.global_desc_1, [-1, self.n_thetas * self.n_rhos * self.n_feat]
                )
        
        self.global_desc_1 = tf.keras.layers.Dense(
                    self.n_thetas * self.n_rhos,
                    activation=tf.nn.relu,
                )(self.global_desc_1)

        self.global_desc_1 = tf.matmul(
                    tf.transpose(self.global_desc_1), self.global_desc_1
                ) / tf.cast(tf.shape(self.global_desc_1)[0], tf.float32)
        self.global_desc_2 = self.global_desc_1
        # self.global_desc_2 = self.global_desc_1
        # self.global_desc_2 = self.global_desc_1
        self.global_desc_1 = tf.reshape(self.global_desc_1, [1, -1])
        self.global_desc_1 = tf.nn.dropout(self.global_desc_1, self.keep_prob)
        self.global_desc_1 = tf.keras.layers.Dense(
            64, activation=tf.nn.relu
        )(self.global_desc_1)
        
        self.logits = tf.keras.layers.Dense(
                    self.n_ligands, activation=tf.identity
        )(self.global_desc_1)
        
        return self.global_desc_2, self.logits, self.rho_coords2

    def inference(
        self,
        input_feat, # learning_obj.input_feat
        rho_coords, # learning_obj.rho_coords
        theta_coords,
        mask,
        W_conv,
        b_conv,
        mu_rho,
        sigma_rho,
        mu_theta,
        sigma_theta,
        eps=1e-5,
        mean_gauss_activation=True,
    ):
        n_samples = tf.shape(rho_coords)[0]
        n_vertices = tf.shape(rho_coords)[1]
      

        all_conv_feat = []
        for k in range(self.n_rotations):
            print("\trotation", k+1)
            rho_coords_ = tf.reshape(rho_coords, [-1, 1])  # batch_size*n_vertices
            thetas_coords_ = tf.reshape(theta_coords, [-1, 1])  # batch_size*n_vertices

            thetas_coords_ += k * 2 * np.pi / self.n_rotations
            thetas_coords_ = tf.math.mod(thetas_coords_, 2 * np.pi)
            rho_coords_ = tf.exp(
                -tf.square(rho_coords_ - mu_rho) / (tf.square(sigma_rho) + eps)
            )
            thetas_coords_ = tf.exp(
                -tf.square(thetas_coords_ - mu_theta) / (tf.square(sigma_theta) + eps)
            )
            
            gauss_activations = tf.multiply(
                rho_coords_, thetas_coords_
            )  # batch_size*n_vertices, n_gauss
            # print("gauss_activations shape 1",gauss_activations.shape)
            
            gauss_activations = tf.reshape(
                gauss_activations, [n_samples, n_vertices, -1]
            )  # batch_size, n_vertices, n_gauss
            # print("gauss_activations shape 2",gauss_activations.shape)
            gauss_activations = tf.multiply(gauss_activations, mask)
            
            if (
                mean_gauss_activation
            ):  # computes mean weights for the different gaussians
                gauss_activations /= (
                    tf.reduce_sum(gauss_activations, 1, keepdims=True) + eps
                )  # batch_size, n_vertices, n_gauss
            
            gauss_activations = tf.expand_dims(
                gauss_activations, 2
            )  # batch_size, n_vertices, 1, n_gauss,
            input_feat_ = tf.expand_dims(
                input_feat, 3
            )  # batch_size, n_vertices, n_feat, 1

            gauss_desc = tf.multiply(
                gauss_activations, input_feat_
            )  # batch_size, n_vertices, n_feat, n_gauss,
            
            gauss_desc = tf.reduce_sum(gauss_desc, 1)  # batch_size, n_feat, n_gauss,
            gauss_desc = tf.reshape(
                gauss_desc, [n_samples, self.n_thetas * self.n_rhos]
            )  # batch_size, 80
            
            
            conv_feat = tf.matmul(gauss_desc, W_conv) + b_conv  # batch_size, 80
            rho_coords2 = tf.identity(conv_feat)
            all_conv_feat.append(conv_feat)

        all_conv_feat = tf.stack(all_conv_feat)
        conv_feat = tf.reduce_max(all_conv_feat, 0)
        conv_feat = tf.nn.relu(conv_feat)
        return conv_feat, rho_coords2


    def compute_initial_coordinates(self):
        range_rho = [0.0, self.max_rho]
        range_theta = [0, 2 * np.pi]

        grid_rho = np.linspace(range_rho[0], range_rho[1], num=self.n_rhos + 1)
        grid_rho = grid_rho[1:]
        grid_theta = np.linspace(range_theta[0], range_theta[1], num=self.n_thetas + 1)
        grid_theta = grid_theta[:-1]

        grid_rho_, grid_theta_ = np.meshgrid(grid_rho, grid_theta, sparse=False)
        grid_rho_ = (
            grid_rho_.T
        )  # the traspose here is needed to have the same behaviour as Matlab code
        grid_theta_ = (
            grid_theta_.T
        )  # the traspose here is needed to have the same behaviour as Matlab code
        grid_rho_ = grid_rho_.flatten()
        grid_theta_ = grid_theta_.flatten()

        coords = np.concatenate((grid_rho_[None, :], grid_theta_[None, :]), axis=0)
        coords = coords.T  # every row contains the coordinates of a grid intersection
        print(coords.shape)
        return coords

In [153]:
tf.keras.utils.set_random_seed(
    0
)

global_desc_2, logits, rho_coords2 = MaSIF_ligand2(
    max_rho=params["max_distance"],
    n_ligands=params["n_classes"],
    feat_mask=params["feat_mask"],
    n_rotations=2
)([input_feat,rho_coords,theta_coords,mask,pocket_labels,tf.constant(1.0)])

logits

(80, 2)
[[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 2. 2. 2. 2. 2. 2. 2. 2.
  2. 2. 2. 2. 2. 2. 2. 2. 3. 3. 3. 3. 3. 3. 3. 3. 3. 3. 3. 3. 3. 3. 3. 3.
  4. 4. 4. 4. 4. 4. 4. 4. 4. 4. 4. 4. 4. 4. 4. 4. 5. 5. 5. 5. 5. 5. 5. 5.
  5. 5. 5. 5. 5. 5. 5. 5.]]
feature si
	rotation 1
	rotation 2
feature ddc
	rotation 1
	rotation 2
feature hbond
	rotation 1
	rotation 2
feature charge
	rotation 1
	rotation 2
feature hphob
	rotation 1
	rotation 2


<tf.Tensor: shape=(1, 10), dtype=float32, numpy=array([[0., 0., 0., 0., 0., 0., 0., 0., 0., 0.]], dtype=float32)>

In [171]:
# global_desc_1= tf.matmul(
#                     tf.transpose(global_desc_2), global_desc_2
#                 ) / tf.cast(tf.shape(global_desc_2)[0], tf.float32)
global_desc_1 = tf.reshape(global_desc_2, [1, -1])
print(global_desc_1.numpy().sum())
global_desc_1 = tf.nn.dropout(global_desc_1, 0)
print(global_desc_1.numpy().sum())
global_desc_1 = tf.keras.layers.Dense(
                    # self.global_desc_1, 
                    64, activation=tf.nn.relu
                )(global_desc_1)
print(global_desc_1.numpy().sum())
logits = tf.keras.layers.Dense(
                    # self.global_desc_1, 
                    10, activation=tf.identity
                )(global_desc_1)
logits.numpy()

119.62979
119.62979
2.1289468


array([[-0.0555419 ,  0.03970499,  0.12917554,  0.01918199,  0.03854598,
        -0.0966502 , -0.07949439, -0.02372705,  0.03092936,  0.08310579]],
      dtype=float32)

In [17]:
tf.compat.v1.set_random_seed(1)
W_conv = []
# initializer=tf.keras.initializers.glorot_normal(seed=10)
for i in range(5):
    
    W_conv.append(
            glorot_uniform((80, 80), seed=(i+1)*100)
                        
    )
[i.sum() for i in W_conv]  

[-1.5037203, -8.606368, 11.876073, -4.781926, 5.059454]

In [242]:
tf.compat.v1.set_random_seed(1)
W_conv = []
initializer=tf.compat.v1.keras.initializers.glorot_normal(seed=10)
# initializer=tf.keras.initializers.glorot_normal(seed=10)
for i in range(5):
    W_conv.append(
           initializer(shape=(80, 80))
    )
[i.numpy().sum() for i in W_conv]

[-13.312803, -13.312803, -13.312803, -13.312803, -13.312803]

In [4]:
params["n_classes"]=10

layer = MaSIF_ligand2(
    max_rho=params["max_distance"],
    n_ligands=params["n_classes"],
    feat_mask=params["feat_mask"]
)
# _ = layer(ops.zeros((1, 1)))

NameError: name 'params' is not defined

In [50]:
from masif_modules.read_ligand_tfrecords import _parse_function

params = masif_opts["ligand"]

# Load dataset
training_data = tf.data.TFRecordDataset(
    os.path.join(params["tfrecords_dir"], "training_data.tfrecord")
)
validation_data = tf.data.TFRecordDataset(
    os.path.join(params["tfrecords_dir"], "validation_data.tfrecord")
)
testing_data = tf.data.TFRecordDataset(
    os.path.join(params["tfrecords_dir"], "testing_data.tfrecord")
)
training_data = training_data.map(_parse_function)
validation_data = validation_data.map(_parse_function)
testing_data = testing_data.map(_parse_function)

tf.random.set_seed(0)
training_iterator = iter(training_data)
# training_iterator=training_data.make_one_shot_iterator()
# data_element = training_iterator.get_next()
# data_element[5]

In [74]:
from collections import OrderedDict
import pymesh
import numpy as np
import sys
test = [x.rstrip().split('.')[0] for x in open("feat.txt").readlines()]
# training_list = [x.rstrip() for x in open(params['training_list']).readlines()]


In [75]:
my_dict = {}
len(test)

10522

In [159]:
f

'Sim_1_traj_21_frame_126'

In [162]:
"data_preparation/01-benchmark_surfaces/"+f+"_protein.ply"

'data_preparation/01-benchmark_surfaces/Sim_1_traj_21_frame_132_protein.ply'

In [161]:
from collections import OrderedDict
import pymesh
import numpy as np
import sys

test = [x.rstrip().split('.')[0] for x in open("names.txt").readlines()]
my_dict = {}

for i, f in enumerate(test[3300:3600]):
    if i % 10 == 0:
        print(i,f)
        sys.stdout.flush()
    m=pymesh.load_mesh("data_preparation/01-benchmark_surfaces/"+f+"_protein.ply")
    n=np.load("data_preparation/01-benchmark_surfaces/"+f+"_names.npy",
        allow_pickle=True).item()['names1']

    one = n[m.get_attribute("vertex_iface")==1]
    if len(one) > 0:
        if len(one.shape) > 1:
            one = np.concatenate(one)
        one = ['_'.join(np.array(i.split('_'))[1:4]) for i in one]
        if '384_x_TYR' in one:
            print(f)
        for name in one:
            if name in my_dict:
                my_dict[name]['1'] +=1
            else:
                my_dict[name] = {}
                my_dict[name]['1'] = 1
            if '2' not in my_dict[name]:
                my_dict[name]['2'] = 0
    two = n[m.get_attribute("vertex_iface")==2]
    if len(two) > 0:
        two = ['_'.join(np.array(i.split('_'))[1:4]) for i in np.concatenate(two)]
        for name in two:
            if name in my_dict:
                my_dict[name]['2'] +=1
            else:
                my_dict[name] = {}
                my_dict[name]['2'] = 1
        
res = OrderedDict(sorted(my_dict.items(),
       key = lambda x: x[1]['2'], reverse=True))
np.save("two.npy", res)
res = OrderedDict(sorted(my_dict.items(),
       key = lambda x: x[1]['1'], reverse=True))
np.save("one.npy", res)


0 Sim_1_traj_21_frame_115
10 Sim_1_traj_21_frame_1200
20 Sim_1_traj_21_frame_1228
30 Sim_1_traj_21_frame_1257
40 Sim_1_traj_21_frame_1283


RPly: Error reading 'vertex_indices' of 'face' number 14671


RuntimeError: PLY parsing failed

In [90]:
my_dict

{'347_x_PRO': {'1': 195, '2': 0},
 '352_x_GLN': {'1': 115, '2': 0},
 '354_x_ALA': {'1': 363, '2': 0},
 '353_x_PHE': {'1': 82, '2': 0},
 '345_x_ILE': {'1': 86, '2': 0},
 '207_x_ILE': {'1': 575, '2': 0},
 '356_x_ILE': {'1': 252, '2': 0},
 '282_x_HIS': {'1': 362, '2': 0},
 '281_x_ARG': {'1': 132, '2': 0},
 '278_x_ASP': {'1': 14, '2': 0},
 '191_x_LEU': {'1': 406, '2': 0},
 '350_x_LYS': {'1': 25, '2': 0},
 '284_x_ASN': {'1': 141, '2': 0},
 '380_x_TYR': {'1': 101, '2': 0},
 '305_x_GLY': {'1': 63, '2': 0},
 '306_x_ASN': {'1': 169, '2': 0},
 '338_x_VAL': {'1': 52, '2': 0},
 '381_x_ALA': {'1': 74, '2': 0},
 '307_x_GLY': {'1': 18, '2': 0},
 '236_x_THR': {'1': 170, '2': 0},
 '188_x_LEU': {'1': 195, '2': 0},
 '193_x_LEU': {'1': 269, '2': 0},
 '189_x_PRO': {'1': 190, '2': 0},
 '192_x_LYS': {'1': 283, '2': 0},
 '196_x_GLU': {'1': 160, '2': 0},
 '235_x_PHE': {'1': 1302, '2': 0},
 '237_x_ASP': {'1': 157, '2': 0},
 '287_x_LEU': {'1': 18, '2': 0},
 '290_x_TYR': {'1': 11, '2': 0},
 '292_x_ILE': {'1': 67,

In [92]:
from collections import OrderedDict
res = OrderedDict(sorted(my_dict.items(),
       key = lambda x: x[1]['2'], reverse=True))
res
np.save("two.npy", res)

In [91]:
res=np.load("one.npy", allow_pickle=True).item()
res

OrderedDict([('384_x_TYR', {'1': 1842, '2': 0}),
             ('227_x_ARG', {'1': 1812, '2': 0}),
             ('330_x_LEU', {'1': 1603, '2': 0}),
             ('304_x_PRO', {'1': 1550, '2': 0}),
             ('255_x_LYS', {'1': 1518, '2': 0}),
             ('235_x_PHE', {'1': 1302, '2': 0}),
             ('302_x_CYS', {'1': 1253, '2': 0}),
             ('230_x_HIS', {'1': 1243, '2': 0}),
             ('223_x_GLY', {'1': 983, '2': 0}),
             ('226_x_VAL', {'1': 951, '2': 0}),
             ('195_x_LEU', {'1': 579, '2': 0}),
             ('207_x_ILE', {'1': 575, '2': 0}),
             ('286_x_LYS', {'1': 437, '2': 0}),
             ('191_x_LEU', {'1': 406, '2': 0}),
             ('252_x_ARG', {'1': 394, '2': 0}),
             ('382_x_THR', {'1': 385, '2': 0}),
             ('559_x_LEU', {'1': 378, '2': 0}),
             ('354_x_ALA', {'1': 363, '2': 0}),
             ('282_x_HIS', {'1': 362, '2': 0}),
             ('249_x_LYS', {'1': 360, '2': 0}),
             ('251_x_ILE', {'1':

In [61]:
dict(sorted(my_dict.items(), key = lambda x: x['1']))

TypeError: tuple indices must be integers or slices, not str

In [56]:
my_dict

{'208_x_CYS': {'1': 214, '2': 0},
 '201_x_CYS': {'1': 168, '2': 0},
 '254_x_ASP': {'1': 75, '2': 1},
 '385_x_ALA': {'1': 166, '2': 2},
 '210_x_VAL': {'1': 242, '2': 0},
 '575_x_AKG': {'1': 262, '2': 3},
 '209_x_VAL': {'1': 200, '2': 0},
 '301_x_ALA': {'1': 185, '2': 1},
 '327_x_ILE': {'1': 128, '2': 0},
 '198_x_ILE': {'1': 319, '2': 3},
 '197_x_TYR': {'1': 237, '2': 1},
 '329_x_TYR': {'1': 45, '2': 0},
 '299_x_MET': {'1': 175, '2': 4},
 '252_x_ARG': {'1': 103, '2': 1},
 '256_x_ILE': {'1': 15, '2': 0},
 '389_x_TRP': {'1': 54, '2': 1},
 '386_x_ILE': {'1': 112, '2': 2},
 '300_x_VAL': {'1': 54, '2': 1},
 '303_x_TYR': {'1': 10, '2': 0},
 '383_x_ARG': {'1': 62, '2': 0},
 '387_x_THR': {'1': 146, '2': 0},
 '193_x_LEU': {'1': 34, '2': 0},
 '384_x_TYR': {'1': 33, '2': 0},
 '365_x_PHE': {'1': 241, '2': 3},
 '226_x_VAL': {'1': 20, '2': 0},
 '302_x_CYS': {'1': 40, '2': 0},
 '230_x_HIS': {'1': 64, '2': 0},
 '382_x_THR': {'1': 30, '2': 1},
 '227_x_ARG': {'1': 19, '2': 0},
 '363_x_LEU': {'1': 135, '2'

2024-07-22 22:42:56.688901: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-07-22 22:42:56.726912: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-07-22 22:42:57.404396: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


Setting cache_dir to nn_models/sc05/cache/ 
Setting model_dir to nn_models/sc05/all_feat/model_data/ 
Setting desc_dir to output/sc05/all_feat/model_data/ 
Setting gif_eval_out to nn_models/sc05/gif_eval/ 
Setting min_sc_filt to 0.5 
Setting max_sc_filt to 1.0 
Setting pos_surf_accept_probability to 1.0 


In [59]:
import pymesh
mesh=pymesh.load_mesh("data_preparation/01-benchmark_surfaces/Sim_1_traj_10_frame_1282_protein.ply")
(mesh.get_attribute('vertex_iface')==1).sum()


79

In [75]:
precom_dir = params["masif_precomputation_dir"]
ligand_coord_dir = params["ligand_coords_dir"]
tfrecords_dir = params["tfrecords_dir"]
params["n_classes"]=10

tf.random.set_seed(0)
for num_train_sample in range(1):
# for num_train_sample in range(int(num_training_samples / 10)):
    try:
        # data_element = training_iterator.get_next()
        data_element = list(training_iterator)[0]
    except Exception as e:
        print(e)
    labels = data_element[4]
    print(data_element[5])
    n_ligands = labels.shape[1]
    # Choose a random ligand from the structure
    all_ligand_types = np.load(
        os.path.join(
            ligand_coord_dir, "{}_ligtypes.npy".format(data_element[5].numpy().decode("utf-8"))
        )
    ).astype(str)
    # random_ligand = np.random.choice(n_ligands, 1) # TODO: don't choose cofactor?
    
    random_ligand = np.random.choice(n_ligands-1, 1)+1 # TODO: don't choose cofactor?
    pocket_points = np.where(labels.numpy()[:, random_ligand] != 0.0)[0]
    label = np.max(labels.numpy()[:, random_ligand]) - 1
    pocket_labels = np.zeros(params["n_classes"], dtype=np.float32)
    pocket_labels[label] = 1.0
    npoints = pocket_points.shape[0]
    if npoints < 32:
        print('less than 32:', npoints, data_element[5], all_ligand_types[random_ligand])
        continue
    else:
        print(npoints, data_element[5], all_ligand_types[random_ligand])

    input_feat=data_element[0].numpy()[pocket_points[:32], :, :]
    rho_coords=np.expand_dims(data_element[1], -1)[pocket_points[:32], :, :]
    theta_coords=np.expand_dims(data_element[2], -1)[pocket_points[:32], :, :]
    mask=data_element[3].numpy()[pocket_points[:32], :, :]

list index out of range
tf.Tensor(b'Sim_1_traj_10_frame_1282', shape=(), dtype=string)
38 tf.Tensor(b'Sim_1_traj_10_frame_1282', shape=(), dtype=string) [['O2IF' 'res_595']]


2024-07-22 23:40:46.112046: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


In [76]:
input_feat.shape

(32, 50, 5)

In [168]:
# feed_dict = {
#         'Input_feat': input_feat,
#         'rho_coords':rho_coords,
#         'theta_coords': theta_coords,
#         'mask': mask,
#         'labels': pocket_labels,
#         'keep_prob': 1.0
#     }
# feed_dict = [input_feat,rho_coords,theta_coords,mask,pocket_labels,1.0]

global_desc_1, rho_coords2 = MaSIF_ligand2(
    max_rho=params["max_distance"],
    n_ligands=params["n_classes"],
    feat_mask=params["feat_mask"],
    n_rotations=2
)([input_feat,rho_coords,theta_coords,mask,pocket_labels,tf.constant(1.0)])

(80, 2)
[[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 2. 2. 2. 2. 2. 2. 2. 2.
  2. 2. 2. 2. 2. 2. 2. 2. 3. 3. 3. 3. 3. 3. 3. 3. 3. 3. 3. 3. 3. 3. 3. 3.
  4. 4. 4. 4. 4. 4. 4. 4. 4. 4. 4. 4. 4. 4. 4. 4. 5. 5. 5. 5. 5. 5. 5. 5.
  5. 5. 5. 5. 5. 5. 5. 5.]]
feature si
	rotation 1
	rotation 2
feature ddc
	rotation 1
	rotation 2
feature hbond
	rotation 1
	rotation 2
feature charge
	rotation 1
	rotation 2
feature hphob
	rotation 1
	rotation 2


In [43]:


batch_size=200
params["n_conv_layers"]=1

ppi_pair_id="Sim_1_traj_42_frame_1307"
mydir="data_preparation/04a-precomputation_12A/precomputation/" + ppi_pair_id + "/"
pdbid = ppi_pair_id.split(".")[0]
pid=pdbid
rho_wrt_center = np.load(mydir + pid + "_rho_wrt_center.npy")
theta_wrt_center = np.load(mydir + pid + "_theta_wrt_center.npy")
input_feat = np.load(mydir + pid + "_input_feat.npy")

iface_labels = np.load(mydir + pid + "_iface_labels.npy")

mask = np.load(mydir + pid + "_mask.npy")
mask = np.expand_dims(mask, 2)
indices = np.load(mydir + pid + "_list_indices.npy", allow_pickle=True).item()['protein']

# indices is (n_verts x <30), it should be
# indices = pad_indices(indices, mask.shape[1])
tmp = np.zeros((len(iface_labels), 3))
for i in range(len(iface_labels)):
    if iface_labels[i] == 1:
        tmp[i, 1] = 1
    elif iface_labels[i] == 2:
        tmp[i, 2] = 1
    else:
        tmp[i, 0] = 1
iface_labels_dc = tmp
super_pos = np.where(iface_labels == 2)[0]
pos_labels = np.where(iface_labels == 1)[0]
neg_labels = np.where(iface_labels == 0)[0]
print("PNS",len(pos_labels),len(neg_labels), len(super_pos))


n = min(len(pos_labels), len(neg_labels))
n = min(n, batch_size // 2)
subset = np.concatenate([neg_labels[:(n*5)], pos_labels[:n], super_pos])
print(len(subset))

NameError: name 'params' is not defined

In [ ]:
for num_train_sample in range(1):
# for num_train_sample in range(int(num_training_samples / 10)):
    try:
        data_element = sess.run(training_next_element)
    except Exception as e:
        print(e)
    labels = data_element[4]
    n_ligands = labels.shape[1]
    # Choose a random ligand from the structure
    all_ligand_types = np.load(
        os.path.join(
            ligand_coord_dir, "{}_ligtypes.npy".format(data_element[5].decode("utf-8"))
        )
    ).astype(str)
    random_ligand = np.random.choice(n_ligands, 1) # TODO: don't choose cofactor?
    pocket_points = np.where(labels[:, random_ligand] != 0.0)[0]
    label = np.max(labels[:, random_ligand]) - 1
    pocket_labels = np.zeros(params["n_classes"], dtype=np.float32)
    pocket_labels[label] = 1.0
    npoints = pocket_points.shape[0]
    if npoints < 32:
        print('less than 32:', npoints, data_element[5], all_ligand_types[random_ligand])
        continue
    else:
        print(npoints, data_element[5], all_ligand_types[random_ligand])

    input_feat=data_element[0][pocket_points[:32], :, :]
    rho_coords=np.expand_dims(data_element[1], -1)[pocket_points[:32], :, :]
    theta_coords=np.expand_dims(data_element[2], -1)[pocket_points[:32], :, :]
    mask=data_element[3][pocket_points[:32], :, :]

In [59]:
from masif_modules.read_ligand_tfrecords import _parse_function
# Load dataset
training_data = tf.data.TFRecordDataset(
    os.path.join(params["tfrecords_dir"], "training_data.tfrecord")
)
training_data = training_data.map(_parse_function)
# training_iterator = training_data.make_one_shot_iterator()
# training_next_element = training_iterator.get_next()

batched_dataset

In [53]:
batched_dataset

<_BatchDataset element_spec=(TensorSpec(shape=(None, None, None, None), dtype=tf.float32, name=None), TensorSpec(shape=(None, None, None), dtype=tf.float32, name=None), TensorSpec(shape=(None, None, None), dtype=tf.float32, name=None), TensorSpec(shape=(None, None, None, None), dtype=tf.float32, name=None), TensorSpec(shape=(None, None, None), dtype=tf.int64, name=None), TensorSpec(shape=(None,), dtype=tf.string, name=None))>

In [51]:
from input_output.save_ply import save_ply
save_ply("mesh_test"+".ply", mesh.vertices,
         mesh.faces, normals=n, 
         charges=mesh.get_attribute("vertex_charge"),
         normalize_charges=False, 
         hbond=mesh.get_attribute("vertex_hbond"), 
         hphob=mesh.get_attribute("vertex_hphob"),
         iface=mesh.get_attribute("vertex_iface"))

In [23]:
from masif_modules.read_data_from_surface import read_data_from_surface, compute_shape_complementarity
import os
import sys
import re
import numpy as np

params = masif_opts['site']
masif_opts["ply_file_template"] = masif_opts["ply_chain_dir"] + "/{}_{}.ply"

print(masif_opts['ply_file_template'])
# plane 7037
ppi_pair_list=['1A0H_D']
for ppi_pair_id in ppi_pair_list:
    print(ppi_pair_id)
    all_list_desc = []
    all_list_coords = []
    all_list_shape_idx = []
    all_list_names = []
    idx_positives = []
    # fields=ppi_pair_id.split('.')
    fields=ppi_pair_id.split('_')

    my_precomp_dir = params['masif_precomputation_dir']
    if not os.path.exists(my_precomp_dir):
        os.makedirs(my_precomp_dir)

    ply_file = {}
    ply_file['p1'] = masif_opts['ply_file_template'].format(fields[0], fields[1])
    if len (fields) == 2 or fields[2] == '':
        pids = ['p1']
    
    rho = {}
    neigh_indices = {}
    mask = {}
    input_feat = {}
    theta = {}
    iface_labels = {}
    verts = {}

    pid=pids[0]
    print(ply_file[pid])
    (input_feat[pid], 
     rho[pid], 
     theta[pid], 
     mask[pid], 
     neigh_indices[pid], 
     iface_labels[pid], 
     verts[pid]) = read_data_from_surface(ply_file[pid], 
                                          params, 
                                          fields[0])

data_preparation/01-benchmark_surfaces//{}_{}.ply
1A0H_D
data_preparation/01-benchmark_surfaces//1A0H_D.ply
data_preparation/04a-precomputation_9A/precomputation//1A0H_theta.npy
params[max_distance] 9.0


OSError: File not found: data_preparation/01-benchmark_surfaces//1A0H_D.ply

In [11]:
pdb='Sim_1_traj_10_frame_1236'
regular_mesh=pymesh.load_mesh('data_preparation/01-benchmark_surfaces/%s_protein.ply' % pdb)
regular_mesh.get_attribute("vertex_iface").sum()

# full_regular_mesh=pymesh.load_mesh('data_preparation/01-benchmark_surfaces/%s_protein_complex.ply' % pdb)
# full_regular_mesh.get_attribute("vertex_iface").sum()

regular_names = np.load('data_preparation/01-benchmark_surfaces/%s_names.npy' % pdb, allow_pickle=True).item()

full_regular_names = np.load('data_preparation/01-benchmark_surfaces/%s_fullnames.npy' % pdb, allow_pickle=True).item()

regular_names=np.concatenate(regular_names['names1'])
full_regular_names=full_regular_names['names1']
print(len(full_regular_names), len(regular_names))

55599 7248


In [46]:
# Neural network ligand application specific parameters.
import os
import sys
from multiprocessing import Pool
import subprocess as sp
import itertools

sys.path.insert(0, "/data/pompei/bw973/Oxygenases/masif/source")
from default_config.masif_opts import masif_opts
masif_opts["ply_file_template"] = masif_opts["ply_chain_dir"] + "/{}_protein.ply"
masif_opts["ligand"] = {}
masif_opts["ligand"]["assembly_dir"] = "data_preparation/00b-pdbs_assembly/"
masif_opts["ligand"]["assembly_dir2"] = "data_preparation/00c-pdbs_assembly/"
masif_opts["ligand"]["ligand_coords_dir"] = "data_preparation/00c-ligand_coords/"
masif_opts["ligand"][
    "masif_precomputation_dir"
] = "data_preparation/04a-precomputation_12A/precomputation/"
masif_opts["ligand"]["max_shape_size"] = 50
masif_opts["ligand"]["feat_mask"] = [1.0] * 5
masif_opts["ligand"]["train_fract"] = 0.9 * 0.8
masif_opts["ligand"]["val_fract"] = 0.1 * 0.8
masif_opts["ligand"]["test_fract"] = 0.2
masif_opts["ligand"]["tfrecords_dir"] = "data_preparation/tfrecords/"
masif_opts["ligand"]["max_distance"] = 5.0
masif_opts["ligand"]["n_classes"] = 7
masif_opts["ligand"]["feat_mask"] = [1.0, 1.0, 1.0, 1.0, 1.0]
masif_opts["ligand"]["costfun"] = "dprime"
masif_opts["ligand"]["model_dir"] = "nn_models/all_feat/"
masif_opts["ligand"]["test_set_out_dir"] = "test_set_predictions/"

def convert_to_string(binary):
    return binary.decode('utf-8')

def _run_command(cmd_info):
    """Helper function for submitting commands parallelized."""
    cmd, supress = cmd_info
    p = sp.Popen(cmd, shell=True, stdout=sp.PIPE, stderr=sp.PIPE)
    output, err = p.communicate()
    if convert_to_string(err) != '' and not supress:
        print("\nERROR: " + convert_to_string(err))
        raise
    output = convert_to_string(output)
    p.terminate()
    return output


def run_commands(cmds, supress=False, n_procs=1):
    """Wrapper for submitting commands to shell"""
    if type(cmds) is str:
        cmds = [cmds]
    if n_procs == 1:
        outputs = []
        for cmd in cmds:
            outputs.append(_run_command((cmd, supress)))
    else:
        cmd_info = list(zip(cmds, itertools.repeat(supress)))
        pool = Pool(processes = n_procs)
        outputs = pool.map(_run_command, cmd_info)
        pool.terminate()
    return outputs

from multiprocessing import Pool

# pool = Pool(processes=5)
# _ = pool.map(preprocess, range(1,6))

In [50]:
# need to preprocess to only select O2 within 3.5 angstroms of protein
import mdtraj as md
import numpy as np
import scipy
from subprocess import Popen, PIPE
import subprocess as sp
from biopandas.pdb import PandasPdb
import sys

# which frames have O2IF within 2.5 angstroms


def cmap_per_residue(traj,sel_list,ref_list,cutoff=3.5,metric='euclidean'):
    if len(ref_list)==0 or len(sel_list)==0:
        print("One of the selections is empty")
        return []
    coord1 = traj.xyz[:,sel_list,:]*10.0 # gas
    coord2 = traj.xyz[:,ref_list,:]*10.0 # protein
    residue_sel = np.array([traj.topology.atom(ind).residue.index for ind in sel_list]) # gas
    residue_ref = np.array([traj.topology.atom(ind).residue.index for ind in ref_list])
    residue_sel_un = np.unique(residue_sel) # gas
    residue_ref_un = np.unique(residue_ref)
    dic_sel={t:c  for c,t in enumerate(residue_sel_un)} # gas
    dic_ref={t:c  for c,t in enumerate(residue_ref_un)}
    histo = np.zeros((len(coord1),len(residue_sel_un),len(residue_ref_un)))
    for c,j in enumerate(coord1):
        axis_sel,axis_ref = np.where(scipy.spatial.distance.cdist(coord1[c],coord2[c],metric=metric) < cutoff)
        real_a= residue_sel[axis_sel]
        real_b= residue_ref[axis_ref]
        elements,counts = np.unique(list(zip(real_a,real_b)),axis=0,return_counts=True)
        for c1,el in enumerate(elements):
            ax1=dic_sel[el[0]];
            ax2=dic_ref[el[1]];
            histo[c,ax1,ax2] = counts[c1];
    return residue_sel_un,residue_ref_un,histo

# gas = sys.argv[1]
gas = 'O2IF'
gases_ligands = ['O2I','N2I','O2Q','N2']#, 'AKG'
simnum=1
trjnum=1
# top = '/data/pompei/bw973/Oxygenases/PHD2/PHD2_50_O2IF/Bundle/Sim%d/equil5.gro' % simnum
nfrcond=1
lengths = []
top = 'equil5.gro'
# trjconv -f $i -s run1.tpr -o an$number.xtc -pbc mol -ur compact -center <<< "14 0"
# for trjnum in range(1, 5):
def preprocess(trjnum, gas='O2IF',check=False):
    print(trjnum)
    cmds = ["echo '14 0' | gmx trjconv -f run%d -s run1.tpr -o an%d.xtc -pbc mol -ur compact -center" % (trjnum,trjnum)]
    if check:
        if not os.path.exists("an%d.xtc" % trjnum):
            _ = run_commands(cmds, supress=True)
        else:
            print("an%d.xtc exists" % trjnum)
    else:
        print("making an%d.xtc" % trjnum)
        _ = run_commands(cmds, supress=True)
    # args = ["gmx", "trjconv", "-f", 'run%d.xtc' % (trjnum), "-pbc", "mol", "-ur",\
    #      "compact", "-center", '-o', 'an%d.xtc' % (trjnum), "-s", "run1.tpr" ,  "<<<", '14 0']
    # p2 = Popen(args, stdout=PIPE, stderr=PIPE)
    # stdout, stderr = p2.communicate()
    t = '/data/pompei/bw973/Oxygenases/PHD2/PHD2_50_O2IF/Bundle/Sim%d/an%d.xtc' % (simnum,trjnum)
    print("loading centered an%d.xtc" % trjnum)
    traj = md.load(t, top=top)
    time=np.arange(len(traj))*.01
    protein = traj.topology.select('protein')
    gas2 = traj.topology.select('resname %s' % gas)
    AKG = traj.topology.select('resname AKG')

    test = cmap_per_residue(traj,gas2,protein,cutoff=2.5)
    test_akg = cmap_per_residue(traj,gas2,AKG,cutoff=3.87)
    segments_dict = {}
    for i in range(0,24):
        res=test[2][0:,i]
        t=np.zeros(len(traj))
        res_akg=test_akg[2][0:,i]
        
        t[np.concatenate((np.where(res)[0], np.where(res_akg)[0]))] = 1

        segment=[]
        subsegment,subtime,subframe=[],[],[]
        for c,value in enumerate(t):
            if value==0 and len(subsegment)==0:
                subsegment,subtime=[],[]
            elif value==0 and len(subsegment)!=0:
                if len(subsegment) > nfrcond: 
                    segment.append(np.array([subframe,subtime,subsegment]))
                subsegment,subtime,subframe=[],[],[]
            else: 
                subsegment.append(value)
                subtime.append(time[c])
                subframe.append(c)
        if len(subsegment) > nfrcond: segment.append(np.array([subframe,subtime,subsegment]))
        segments_dict[i] = segment

    l=[]
    for k in segments_dict.keys():
        if len(segments_dict[k]) > 0:
            sl = np.concatenate([r[0] for r in segments_dict[k]])
            l.append(np.unique(sl))
    if len(l) > 0:
        frames = np.unique(np.concatenate(l).astype(int))
        fn = frames+1
        print(len(fn))
        lengths.append(len(fn))
    else:
        print(0)
        lengths.append(0)
    np.save('lengths2.npy', lengths)
    trajf=traj[frames]
    print(np.array(frames))

    for i,f in enumerate(frames):
        trajfn = trajf[i]
        l2 = np.array([], dtype=np.int32)
        test2 = cmap_per_residue(trajfn,gas2,protein,cutoff=2.5)
        test2_akg = cmap_per_residue(trajfn,gas2,AKG,cutoff=5.5)
        whr = np.where([j.sum()>0 for j in test2[2][0]])[0]*2
        whr_akg = np.where([j.sum()>0 for j in test2_akg[2][0]])[0]*2
        l2 = np.append(l2, whr)
        l2 = np.append(l2, whr_akg)
        # print(i,f,l2)
        # break
        whr2 = np.concatenate([(n,(n+1)) for n in np.unique(l2)])
        # print(whr2)
        atms = np.sort(np.concatenate((gas2[whr2],AKG,protein)))
        sel = trajfn.atom_slice(atms)
        # atms = np.sort(np.concatenate((gas2[whr2],AKG,protein)))
        # sel = trajfn.atom_slice(atms)
        pdb="Sim_%d_traj_%d_frame_%d" % (simnum, trjnum, f+1)+'.pdb'
        sel.save(masif_opts["ligand"]["assembly_dir"]+'/'+pdb)
        
        ppdb_df = PandasPdb().read_pdb(masif_opts["ligand"]["assembly_dir"]+'/'+pdb)
        o2if = ppdb_df.df['ATOM']
        o2if.loc[o2if.residue_name=='O2I','atom_name'] = np.concatenate([['OI1','OI2']] * (len(o2if.loc[o2if.residue_name=='O2I','atom_name'])//2))
        ppdb_df._df['ATOM'] = o2if[(o2if['residue_name']!='ACE') & (o2if['residue_name']!='HOH')]
        atom = o2if[~o2if.residue_name.isin(gases_ligands)]
        hetatm = o2if[o2if.residue_name.isin(gases_ligands)]
        ppdb_df._df['ATOM'] = atom
        ppdb_df._df['HETATM'] = hetatm
        ppdb_df._df['HETATM'].loc[:,'record_name']='HETATM'
        ppdb_df.to_pdb(masif_opts["ligand"]["assembly_dir"]+'/'+pdb)

        df_atom=ppdb_df._df['ATOM']
        df=ppdb_df._df['HETATM']
        o2i_uniq = np.unique(df[df.residue_name=='O2I'].residue_number)
        o2i_uniq = np.sort(o2i_uniq)

        lig_types = []
        akg_rn = np.unique(df_atom[df_atom.residue_name=='AKG'].residue_number)
        lig_types.append(['AKG','res_%d' % akg_rn])
        [lig_types.append([gas, 'res_%d' % i]) for i in o2i_uniq]
        np.save(masif_opts["ligand"]["ligand_coords_dir"]+pdb.split('.')[0]+'_ligtypes.npy', lig_types)

        lig_coords = {}
        lig_coords[akg_rn[0]] = df[df.residue_name=='AKG'][['x_coord', 'y_coord','z_coord']].values
        for val in o2i_uniq:
            # print(val)
            lig_coords[val] = df[df.residue_number==val][['x_coord', 'y_coord','z_coord']].values

        np.save(masif_opts["ligand"]["ligand_coords_dir"]+pdb.split('.')[0]+'_ligcoords.npy', lig_coords)
    cmds = ["rm an%d.xtc" % (trjnum)]
    run_commands(cmds, supress=True)
# preprocess(trjnum)

import sys
from functools import partial
# python get_close_pdbs.py 2 3 O2IF 2
# processes = int(sys.argv[1])
# rng = int(sys.argv[2])
# pool = Pool(processes=processes)
# gas = sys.argv[3]
# _ = pool.map(partial(preprocess, gas=gas), range(1,1))

In [56]:
top = 'equil5.gro'
t = '/data/pompei/bw973/Oxygenases/PHD2/PHD2_50_O2IF/Bundle/Sim%d/an%d.xtc' % (simnum,trjnum)
print("loading centered an%d.xtc" % trjnum)
traj = md.load(t, top=top)
time=np.arange(len(traj))*.01
protein = traj.topology.select('protein')
gas2 = traj.topology.select('resname %s' % gas)
AKG = traj.topology.select('resname AKG')

test = cmap_per_residue(traj,gas2,protein,cutoff=2.5)
test_akg = cmap_per_residue(traj,gas2,AKG,cutoff=3.87)
segments_dict = {}
for i in range(0,24):
    res=test[2][0:,i]
    t=np.zeros(len(traj))
    res_akg=test_akg[2][0:,i]
    
    t[np.concatenate((np.where(res)[0], np.where(res_akg)[0]))] = 1

    segment=[]
    subsegment,subtime,subframe=[],[],[]
    for c,value in enumerate(t):
        if value==0 and len(subsegment)==0:
            subsegment,subtime=[],[]
        elif value==0 and len(subsegment)!=0:
            if len(subsegment) > nfrcond: 
                segment.append(np.array([subframe,subtime,subsegment]))
            subsegment,subtime,subframe=[],[],[]
        else: 
            subsegment.append(value)
            subtime.append(time[c])
            subframe.append(c)
    if len(subsegment) > nfrcond: segment.append(np.array([subframe,subtime,subsegment]))
    segments_dict[i] = segment

l=[]
for k in segments_dict.keys():
    if len(segments_dict[k]) > 0:
        sl = np.concatenate([r[0] for r in segments_dict[k]])
        l.append(np.unique(sl))
if len(l) > 0:
    frames = np.unique(np.concatenate(l).astype(int))
    fn = frames+1
    print(len(fn))
    lengths.append(len(fn))
else:
    print(0)
    lengths.append(0)
np.save('lengths2.npy', lengths)
trajf=traj[frames]
print(np.array(frames))

loading centered an1.xtc


/home/bw973/.conda/envs/holoprot/lib/python3.10/site-packages/mdtraj/formats/gro.py:322: UserWarning: WARNING: two consecutive residues with same number (GLN, ACE)
  warnings.warn("WARNING: two consecutive residues with same number (%s, %s)" % (thisresname, old_resname))
/home/bw973/.conda/envs/holoprot/lib/python3.10/site-packages/mdtraj/formats/gro.py:322: UserWarning: WARNING: two consecutive residues with same number (ASP, ACE)
  warnings.warn("WARNING: two consecutive residues with same number (%s, %s)" % (thisresname, old_resname))


167
[   2    3    4   79   80  115  116  118  119  131  132  179  180  188
  189  239  240  241  305  306  323  324  326  327  340  341  374  375
  385  386  387  398  399  413  414  418  419  420  431  432  529  530
  545  546  561  562  574  575  647  648  714  715  732  733  734  735
  736  746  747  785  786  803  804  821  822  832  833  848  849  854
  855  869  870  878  879  881  882  886  887  893  894  944  945  962
  963 1098 1099 1100 1102 1103 1125 1126 1130 1131 1146 1147 1156 1157
 1173 1174 1175 1219 1220 1223 1224 1299 1300 1305 1306 1318 1319 1379
 1380 1475 1476 1478 1479 1521 1522 1563 1564 1578 1579 1615 1616 1653
 1654 1658 1659 1697 1698 1716 1717 1736 1737 1738 1756 1757 1762 1763
 1785 1786 1787 1842 1843 1851 1852 1874 1875 1918 1919 1920 1948 1949
 1958 1959 1960 1963 1964 1967 1968 1969 1970 1971 1972 1974 1975]


In [60]:
i,f=list(enumerate(frames))[14]
trajfn = trajf[i]
l2 = np.array([], dtype=np.int32)
test2 = cmap_per_residue(trajfn,gas2,protein,cutoff=2.5)
test2_akg = cmap_per_residue(trajfn,gas2,AKG,cutoff=5.5)
whr = np.where([j.sum()>0 for j in test2[2][0]])[0]*2
whr_akg = np.where([j.sum()>0 for j in test2_akg[2][0]])[0]*2
l2 = np.append(l2, whr)
l2 = np.append(l2, whr_akg)
# print(i,f,l2)
# break
whr2 = np.concatenate([(n,(n+1)) for n in np.unique(l2)])
# print(whr2)
atms = np.sort(np.concatenate((gas2[whr2],AKG,protein)))
sel = trajfn.atom_slice(atms)
# atms = np.sort(np.concatenate((gas2[whr2],AKG,protein)))
# sel = trajfn.atom_slice(atms)
pdb="Sim_%d_traj_%d_frame_%d" % (simnum, trjnum, f+1)+'.pdb'
sel.save(masif_opts["ligand"]["assembly_dir"]+'/'+pdb)

(14, 189)

In [67]:
ppdb_df = PandasPdb().read_pdb(masif_opts["ligand"]["assembly_dir"]+'/'+'Sim_1_traj_1_frame_190.pdb')
o2if = ppdb_df.df['ATOM']
# o2if.loc[o2if.residue_name=='O2I','atom_name'] = np.concatenate([['OI1','OI2']] * (len(o2if.loc[o2if.residue_name=='O2I','atom_name'])//2))
# ppdb_df._df['ATOM'] = o2if[(o2if['residue_name']!='ACE') & (o2if['residue_name']!='HOH')]
atom = o2if[~o2if.residue_name.isin(gases_ligands)]
hetatm = o2if[o2if.residue_name.isin(gases_ligands)]
ppdb_df._df['ATOM'] = atom
ppdb_df._df['HETATM'] = hetatm
ppdb_df._df['HETATM'].loc[:,'record_name']='HETATM'
ppdb_df.to_pdb(masif_opts["ligand"]["assembly_dir"]+'/'+pdb)

df_atom=ppdb_df._df['ATOM']
df=ppdb_df._df['HETATM']
o2i_uniq = np.unique(df[df.residue_name=='O2I'].residue_number)
o2i_uniq = np.sort(o2i_uniq)

lig_types = []
akg_rn = np.unique(df_atom[df_atom.residue_name=='AKG'].residue_number)
lig_types.append(['AKG','res_%d' % akg_rn])
[lig_types.append([gas, 'res_%d' % i]) for i in o2i_uniq]
# np.save(masif_opts["ligand"]["ligand_coords_dir"]+pdb.split('.')[0]+'_ligtypes.npy', lig_types)

lig_coords = {}
lig_coords[akg_rn[0]] = df_atom[df_atom.residue_name=='AKG'][['x_coord', 'y_coord','z_coord']].values

In [72]:
pdbs = glob.glob(masif_opts["ligand"]["assembly_dir"]+'/*.pdb')
# pdbs = [i.split("/")[2] for i in pdbs]
# pdbs
# np.save(masif_opts["ligand"]["ligand_coords_dir"]+pdb.split('.')[0]+'_ligcoords.npy', lig_coords)

In [ ]:
pdb='data_preparation/00b-pdbs_assembly/Sim_1_traj_7_frame_1669.pdb'

In [196]:
for pdb in pdbs[10:]:
# for pdb in ['data_preparation/00b-pdbs_assembly/Sim_1_traj_1_frame_190.pdb']:
    # print(pdb)
    pref=pdb.split("/")[2].split('.')[0]
    print(pref)
    ppdb_df = PandasPdb().read_pdb(pdb)
    df_atom=ppdb_df._df['ATOM']
    lig_coords = np.load(masif_opts["ligand"]["ligand_coords_dir"]+pref+'_ligcoords.npy',
                         allow_pickle=True).item()
    akg_rn = np.unique(df_atom[df_atom.residue_name=='AKG'].residue_number)
    lig_coords[akg_rn[0]] = df_atom[df_atom.residue_name=='AKG'][['x_coord', 'y_coord','z_coord']].values
    # print(lig_coords[akg_rn[0]])
    np.save(masif_opts["ligand"]["ligand_coords_dir"]+pref+'_ligcoords.npy', lig_coords)

Sim_1_traj_49_frame_1924
Sim_1_traj_18_frame_1269
Sim_1_traj_6_frame_244
Sim_1_traj_40_frame_820
Sim_1_traj_10_frame_1502
Sim_1_traj_13_frame_863
Sim_1_traj_32_frame_1646
Sim_1_traj_18_frame_271
Sim_1_traj_18_frame_254
Sim_1_traj_26_frame_3
Sim_1_traj_35_frame_452
Sim_1_traj_8_frame_1476
Sim_1_traj_40_frame_650
Sim_1_traj_6_frame_1636
Sim_1_traj_1_frame_748
Sim_1_traj_4_frame_966
Sim_1_traj_6_frame_637
Sim_1_traj_18_frame_1159
Sim_1_traj_52_frame_1766
Sim_1_traj_1_frame_734
Sim_1_traj_9_frame_1814
Sim_1_traj_23_frame_1430
Sim_1_traj_53_frame_641
Sim_1_traj_18_frame_157
Sim_1_traj_22_frame_1980
Sim_1_traj_9_frame_960
Sim_1_traj_26_frame_537
Sim_1_traj_5_frame_607
Sim_1_traj_24_frame_1796
Sim_1_traj_51_frame_531
Sim_1_traj_8_frame_1466
Sim_1_traj_40_frame_834
Sim_1_traj_40_frame_1224
Sim_1_traj_3_frame_755
Sim_1_traj_7_frame_1589
Sim_1_traj_49_frame_530
Sim_1_traj_35_frame_1504
Sim_1_traj_16_frame_1936
Sim_1_traj_1_frame_1960
Sim_1_traj_48_frame_397
Sim_1_traj_7_frame_1866
Sim_1_traj_18_

In [90]:
lig_coords

{575: array([[36.973, 37.762, 39.438],
        [37.695, 38.591, 38.748],
        [35.953, 37.119, 39.086],
        [37.666, 37.478, 40.77 ],
        [38.846, 37.892, 40.811],
        [37.099, 36.88 , 42.015],
        [37.449, 37.591, 43.313],
        [36.724, 36.994, 44.415],
        [35.795, 36.218, 44.14 ],
        [36.926, 37.392, 45.57 ],
        [37.18 , 38.657, 43.346],
        [38.521, 37.427, 43.498],
        [37.364, 35.812, 41.987],
        [36.032, 36.974, 41.766]]),
 587: array([[32.067, 59.705, 40.524],
        [32.867, 59.867, 39.632]])}

In [22]:
import pymesh
import numpy as np

# test_mesh = pymesh.load_mesh('/data/pompei/bw973/Oxygenases/masif/data/masif_ligand/data_preparation/01-benchmark_surfaces/1IQP_ACBEDF.ply')
test_mesh = pymesh.load_mesh('data_preparation/01-benchmark_surfaces/Sim_2_traj_50_frame_68_protein.ply')
test_mesh.get_attribute("vertex_iface").sum()

132.0

In [ ]:
regular_mesh=pymesh.load_mesh('data_preparation/01-benchmark_surfaces/%s_protein.ply' % pdb)
regular_mesh.get_attribute("vertex_iface").sum()

In [33]:
pdb='Sim_1_traj_10_frame_1556'
regular_mesh=pymesh.load_mesh('data_preparation/01-benchmark_surfaces/%s_protein.ply' % pdb)
regular_mesh.get_attribute("vertex_iface").sum()

full_regular_mesh=pymesh.load_mesh('/tmp/%s_protein_complex.ply' % pdb)
full_regular_mesh.get_attribute("vertex_iface").sum()

regular_names = np.load('data_preparation/01-benchmark_surfaces/%s_names.npy' % pdb, allow_pickle=True).item()

full_regular_names = np.load('data_preparation/01-benchmark_surfaces/%s_fullnames.npy' % pdb, allow_pickle=True).item()

regular_names=regular_names['names1']
full_regular_names=full_regular_names['names1']
print(len(full_regular_mesh.vertices), len(regular_names))

53402 11551


In [32]:
regular_names['names1']

array(['A_275_x_SER_HB3_Green', 'A_390_x_TYR_CE2_Green',
       'A_273_x_MET_HB2_Green', ..., 'A_569_x_ASP_OD2_Red',
       'A_569_x_ASP_OD2_Red', 'A_569_x_ASP_OD2_Red'], dtype='<U22')

In [20]:
from triangulation.computeMSMS import computeMSMS, computeMSMS2
probe='0.70'
vertices1, faces1, normals1, names1, areas1 = computeMSMS2("/tmp/Sim_1_traj_10_frame_1556_protein.pdb",
        protonate=True, probe=probe)

protonating output_pdb_as_xyzrn2 /tmp/Sim_1_traj_10_frame_1556_protein.pdb /tmp/msms_6244006.xyzrn
['/home/bw973/tools/msms/msms', '-density', '3.0', '-hdensity', '3.0', '-probe', '0.70', '-if', '/tmp/msms_6244006.xyzrn', '-of', '/tmp/msms_6244006', '-af', '/tmp/msms_6244006']
file_base /tmp/msms_6244006


In [ ]:
np.where([re.search('AKG',i) for i in regular_names])[0]

In [26]:
full_regular_names

vertices2 = vertices1
faces2 = faces1
from triangulation.computeCharges import computeCharges, assignChargesToNewMesh, assignAtomNamesToNewMesh
from triangulation.fixmesh import fix_mesh
# Step 4: Fix the mesh.
mesh = pymesh.form_mesh(vertices2, faces2)
regular_mesh = fix_mesh(mesh, 0.8)

regular_names = assignAtomNamesToNewMesh(regular_mesh.vertices, 
                                          vertices1, names1) 
regular_names=np.concatenate(regular_names)    
np.where([re.search('AKG',i) for i in regular_names])[0]

Removing degenerated triangles


array([3838, 8849])

In [28]:
len(A)

0

In [15]:
# (regular_mesh.get_attribute("vertex_iface")==2).sum()
(regular_mesh.get_attribute("vertex_iface")==1).sum()
# (regular_mesh.get_attribute("vertex_iface")).sum()
mesh=full_regular_mesh
import re
import scipy

In [16]:
full_iface = np.zeros(len(full_regular_names))
full_iface[np.where([re.search('O2I',i) for i in full_regular_names])[0]] = 1

 # vertices from full mesh with gas/everything
O = np.where([re.search('O2I',i) for i in full_regular_names])[0]
tO=mesh.vertices[O]
# vertices from regular mesh of protein/cofactor
A=np.where([re.search('AKG',i) for i in regular_names])[0]
tA=regular_mesh.vertices[A]

t2=scipy.spatial.distance_matrix(regular_mesh.vertices,tO)
t3=scipy.spatial.distance_matrix(regular_mesh.vertices,tA)
iface1=np.where([(i<3).sum() for i in t2])[0] # protein res near gas
iface2=np.where([(i<5).sum() for i in t3])[0] # protein res near cofactor
iface3=np.where([(i<2).sum() for i in t2])[0] # protein res VERY near gas

In [19]:
A

array([], dtype=int64)

In [12]:
import scipy

t2=scipy.spatial.distance_matrix(regular_mesh.vertices,tO)
# np.where([(i<1).sum() for i in t2])
iface1=regular_names[np.where([(i<3).sum() for i in t2])]
iface1=np.where([(i<3).sum() for i in t2])[0]
len(iface1)
# regular_names

198

In [30]:
regular_mesh.get_attribute("vertex_cofactor_dist").sum()

2938.5756

In [29]:
dist_near_gas_to_AKG[iface1].sum()

2938.57137885261

In [255]:
t3=scipy.spatial.distance_matrix(regular_mesh.vertices,tA)
# np.where([(i<1).sum() for i in t2])

iface2=np.where([(i<5).sum() for i in t3])[0]
len(iface2)
regular_names[np.where([(i<2).sum() for i in t3])]

array(['A_383_x_ARG_CZ_Green', 'A_374_x_HIS_CB_Green',
       'A_575_x_AKG_OG2_Red', 'A_566_x_ILE_HD11_Green',
       'A_327_x_ILE_CG2_Green', 'A_329_x_TYR_OH_Red',
       'A_387_x_THR_OG1_Red', 'A_575_x_AKG_CA_Green',
       'A_575_x_AKG_CG_Green', 'A_252_x_ARG_HH22_Blue',
       'A_315_x_ASP_OD2_Red', 'A_374_x_HIS_CD2_Green',
       'A_327_x_ILE_CD1_Green', 'A_575_x_AKG_OG1_Red',
       'A_383_x_ARG_CZ_Green', 'A_383_x_ARG_HH11_Blue',
       'A_327_x_ILE_HG23_Green', 'A_343_x_LEU_CD1_Green',
       'A_366_x_PHE_HE1_Green', 'A_575_x_AKG_CD_Green',
       'A_575_x_AKG_OE1_Red', 'A_343_x_LEU_CD1_Green',
       'A_387_x_THR_CB_Green', 'A_254_x_ASP_OD1_Red',
       'A_343_x_LEU_HD11_Green', 'A_252_x_ARG_HH11_Blue',
       'A_329_x_TYR_HH_Blue', 'A_252_x_ARG_HH11_Blue',
       'A_313_x_HIS_CE1_Green', 'A_252_x_ARG_HH12_Blue',
       'A_303_x_TYR_HH_Blue', 'A_389_x_TRP_HZ2_Green',
       'A_252_x_ARG_HH21_Blue', 'A_252_x_ARG_HH11_Blue',
       'A_566_x_ILE_HD11_Green', 'A_254_x_ASP_OD2_Red'

In [20]:
regular_names = np.load('data_preparation/01-benchmark_surfaces/%s_names.npy' % pdb, allow_pickle=True).item()['names1']


In [99]:
from masif_modules.read_data_from_surface2 import read_data_from_surface, compute_shape_complementarity
import pymesh
from sklearn.neighbors import KDTree
import numpy as np
from triangulation.fixmesh import fix_mesh
from default_config.masif_opts import masif_opts


params = masif_opts['ligand']



sufs = ['protein','gas']

# pdb=sys.argv[1]
pdb='Sim_1_traj_10_frame_1042'
fields = pdb.split('.')
pid=fields[0]
# masif_app = sys.argv[2]

rho = {}
neigh_indices = {}
mask = {}
input_feat = {}
theta = {}
iface_labels = {}
verts = {}


# for suf in sufs:
    # ply_file = masif_opts["ply_chain_dir"] + "/{}_protein.ply".format(pid)
suf="protein"
p_ply_file = masif_opts["ply_chain_dir"] + "{}_{}.ply".format(pid,suf)
print(p_ply_file)
input_feat[suf], rho[suf], theta[suf], mask[suf], neigh_indices[suf], iface_labels[suf], verts[suf] = read_data_from_surface(p_ply_file, params, pid=pid+"_"+suf)
print(len(verts[suf]))

suf="gas"
g_ply_file = masif_opts["ply_chain_dir"] + "{}_{}.ply".format(pid,suf)
print(g_ply_file)
input_feat[suf], rho[suf], theta[suf], mask[suf], neigh_indices[suf], iface_labels[suf], verts[suf] = read_data_from_surface(g_ply_file, params, False, pid+"_"+suf)
print(len(verts[suf]))

# print(pid)
#         print(ply_file[pid])
#         input_feat[pid], rho[pid], theta[pid], mask[pid], neigh_indices[pid], iface_labels[pid], verts[pid] = read_data_from_surface(ply_file[pid], params, my_precomp_dir+pid)
#         print(len(verts[pid]))
#         pad=params["max_shape_size"]
#         neigh_indices[pid]= np.array([i + [-1]*(pad-len(i)) for i in neigh_indices[pid]])



# pid=pids[0]
# input_feat[pid], rho[pid], theta[pid], mask[pid], neigh_indices[pid], iface_labels[pid], verts[pid] = read_data_from_surface(ply_file[pid], params)

data_preparation/01-benchmark_surfaces/Sim_1_traj_10_frame_1042_protein.ply
data_preparation/04a-precomputation_12A/precomputation//Sim_1_traj_10_frame_1042_protein_theta.npy
params[max_distance] 5.0
params[max_shape_size] 50
Dijkstra took 0.87s
Brian (7187, 7187)
LOADING THETA FROM FILE
data_preparation/04a-precomputation_12A/precomputation//Sim_1_traj_10_frame_1042_protein_theta.npy
extract subpatches
MDS took 0.78s
N~~~~~~~~~~~~~~~= 7187
rho (7187, 50)
vertex_mean_curvature -1.397739357606804 1.195665638630259 -0.013761434648499963
vertex_gaussian_curvature -1.451768001453157 4.527939971507374 0.0346998304174469
elem -3.051368882694251 1.5539301715553977 954.7290776668327
elem 1e-08 1.5539301715553977 1146.5182845118543
si -0.999954453613414 0.999939314105483 238.58229956852435
7187
data_preparation/01-benchmark_surfaces/Sim_1_traj_10_frame_1042_gas.ply
data_preparation/04a-precomputation_12A/precomputation//Sim_1_traj_10_frame_1042_gas_theta.npy
params[max_distance] 5.0
params[max_

In [26]:
regular_mesh=pymesh.load_mesh(p_ply_file)
regular_mesh.get_attribute("vertex_iface")==1

array([False, False, False, ...,  True, False, False])

In [100]:
[len(i) for i in neigh_indices[suf]]

[32,
 30,
 35,
 35,
 35,
 32,
 30,
 35,
 35,
 32,
 35,
 32,
 32,
 34,
 35,
 30,
 30,
 34,
 34,
 33,
 29,
 35,
 32,
 35,
 35,
 32,
 34,
 32,
 34,
 30,
 34,
 32,
 35,
 32,
 30,
 32,
 35,
 30,
 35,
 30,
 30,
 35,
 32,
 32,
 32,
 32,
 32,
 32,
 32,
 30,
 32,
 30,
 35,
 30,
 30,
 35,
 30,
 35,
 32,
 35,
 35,
 35,
 32,
 29,
 30,
 30,
 32,
 30,
 30,
 32,
 30,
 35,
 32,
 30,
 35,
 30,
 35,
 29,
 30,
 30,
 32,
 32,
 34,
 30,
 32,
 32,
 34,
 35,
 29,
 35,
 30,
 32,
 30,
 32,
 32,
 32,
 35]

In [5]:
params = masif_opts['ppi_search']
params

{'training_list': 'lists/training.txt',
 'testing_list': 'lists/testing.txt',
 'max_shape_size': 200,
 'max_distance': 12.0,
 'masif_precomputation_dir': 'data_preparation/04b-precomputation_12A/precomputation/',
 'feat_mask': [1.0, 1.0, 1.0, 1.0, 1.0],
 'max_sc_filt': 1.0,
 'min_sc_filt': 0.5,
 'pos_surf_accept_probability': 1.0,
 'pos_interface_cutoff': 1.0,
 'range_val_samples': 0.9,
 'cache_dir': 'nn_models/sc05/cache/',
 'model_dir': 'nn_models/sc05/all_feat/model_data/',
 'desc_dir': 'descriptors/sc05/all_feat/',
 'gif_descriptors_out': 'gif_descriptors/',
 'sc_radius': 12.0,
 'sc_interaction_cutoff': 1.5,
 'sc_w': 0.25}

In [7]:
params = masif_opts['ligand']
params

{'assembly_dir': 'data_preparation/00b-pdbs_assembly/',
 'ligand_coords_dir': 'data_preparation/00c-ligand_coords/',
 'masif_precomputation_dir': 'data_preparation/04a-precomputation_12A/precomputation/',
 'max_shape_size': 50,
 'feat_mask': [1.0, 1.0, 1.0, 1.0, 1.0],
 'train_fract': 0.7200000000000001,
 'val_fract': 0.08000000000000002,
 'test_fract': 0.2,
 'tfrecords_dir': 'data_preparation/tfrecords/',
 'max_distance': 5.0,
 'n_classes': 7,
 'costfun': 'dprime',
 'model_dir': 'nn_models/all_feat/',
 'test_set_out_dir': 'test_set_predictions/'}

In [27]:
labels[regular_mesh.get_attribute("vertex_iface")==1]

array([0.        , 0.        , 0.        , 0.14597972, 0.        ,
       0.2366637 , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.08355285, 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.03839478, 0.10318743,
       0.        , 0.00771763, 0.10694308, 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.07369141, 0.        ,
       0.        , 0.        , 0.        , 0.00632546, 0.        ,
       0.        , 0.17264761, 0.05035574, 0.        , 0.01729533,
       0.        , 0.        , 0.04360882, 0.        , 0.16040631,
       0.10508836, 0.03987622, 0.        , 0.05922166, 0.23868262,
       0.15804373, 0.06473119, 0.        , 0.04514937, 0.        ,
       0.03074294, 0.        , 0.        , 0.        , 0.04043692,
       0.        , 0.        , 0.        , 0.        , 0.2249412 ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.05940251, 0.        , 0.00782018, 0.     

In [22]:
regular_names
mylabels = p1_sc_labels[0]
labels = np.median(mylabels, axis=1)
np.where((labels < 1) & (labels > 0.5))[0]
            

array([], dtype=int64)

In [108]:
my_precomp_dir+pid+'prot_sc_labels'

'data_preparation/04a-precomputation_12A/precomputation/Sim_1_traj_10_frame_1042prot_sc_labels'

In [109]:
params['sc_w']=0.015
params['sc_interaction_cutoff']=3.0
params['sc_radius']=params['max_distance']
my_precomp_dir = params['masif_precomputation_dir']

p1_sc_labels, p2_sc_labels = compute_shape_complementarity(p_ply_file, g_ply_file, neigh_indices['protein'],neigh_indices['gas'], rho['protein'], rho['gas'], mask['protein'], mask['gas'], params)
np.save(my_precomp_dir+pid+'_prot_sc_labels', p1_sc_labels)
np.save(my_precomp_dir+pid+'_gas_sc_labels', p2_sc_labels)
mylabels = p1_sc_labels[0]
labels = np.median(mylabels, axis=1)
print(labels.max())
labels[regular_mesh.get_attribute("vertex_iface")==1]

0.7382959720670764


array([ 0.19409182,  0.33926028,  0.10185633,  0.55820835,  0.26185184,
        0.52276064,  0.40599038,  0.04924704,  0.19859825,  0.37294294,
        0.33362225,  0.4228295 ,  0.40177565,  0.37393486,  0.23771976,
       -0.06551924,  0.07749214,  0.12544325,  0.27909086,  0.23105103,
        0.31475301,  0.23722981,  0.33752802,  0.18056989, -0.06293532,
        0.00327657,  0.        ,  0.24102007,  0.35256529,  0.12713265,
        0.23837637,  0.39045449,  0.44944485,  0.20612709,  0.18684765,
        0.10850625,  0.45225588,  0.29631758,  0.60863538,  0.23035906,
        0.06467494,  0.26843766,  0.31320666,  0.1088657 ,  0.47368633,
        0.48506486,  0.3296065 ,  0.18119764,  0.37575861,  0.62763063,
        0.45134762,  0.21738169,  0.26064928,  0.55804672,  0.        ,
        0.213009  ,  0.07310514,  0.09562414,  0.33525258,  0.21342182,
        0.11338283,  0.07377811,  0.41790478,  0.16048921,  0.60897764,
        0.        , -0.08243763,  0.4985331 ,  0.32024358,  0.45

In [79]:
(regular_mesh.get_attribute("vertex_iface")==1).sum()

230

In [45]:
regular_names[pos_labels]

array([['A_276_x_MET_O_Red'],
       ['A_193_x_LEU_HD23_Green'],
       ['A_276_x_MET_HA_Green'],
       ['A_280_x_ILE_HD11_Green'],
       ['A_276_x_MET_HB3_Green'],
       ['A_213_x_PHE_CE1_Green'],
       ['A_290_x_TYR_HD1_Green'],
       ['A_276_x_MET_CA_Green'],
       ['A_292_x_ILE_HG13_Green'],
       ['A_276_x_MET_HA_Green'],
       ['A_292_x_ILE_HG13_Green'],
       ['A_287_x_LEU_HD23_Green'],
       ['A_213_x_PHE_HZ_Green'],
       ['A_276_x_MET_HG2_Green'],
       ['A_213_x_PHE_HE1_Green'],
       ['A_326_x_CYS_HG_Green'],
       ['A_193_x_LEU_CD2_Green'],
       ['A_193_x_LEU_HD23_Green']], dtype='<U22')

In [105]:
mylabels = p1_sc_labels[0]
labels = np.median(mylabels, axis=1)
print(pid, labels.max())
labels[regular_mesh.get_attribute("vertex_iface")==1]


pos_labels = np.where(((labels < -0.2) & (labels > -0.6) | (labels > 0.1)))[0]
print(pid,"len(pos_labels)", len(pos_labels))
regular_names[pos_labels]

print(pid, "len_intersect_iface",len(np.intersect1d(
    np.where(regular_mesh.get_attribute("vertex_iface")==1),
    pos_labels
)))

Sim_1_traj_10_frame_1042 len(pos_labels) 174
Sim_1_traj_10_frame_1042 len intersect iface 173


In [62]:
pos_labels = np.where(((labels < 0) & (labels > -0.65) | (labels > 0.65)))[0]
print(len(pos_labels))
regular_names[pos_labels]

71


array([['A_193_x_LEU_HD22_Green'],
       ['A_188_x_LEU_O_Red'],
       ['A_210_x_VAL_HG11_Green'],
       ['A_190_x_ALA_H_Blue'],
       ['A_190_x_ALA_HB2_Green'],
       ['A_285_x_GLY_H_Blue'],
       ['A_326_x_CYS_HG_Green'],
       ['A_326_x_CYS_HB3_Green'],
       ['A_292_x_ILE_CD1_Green'],
       ['A_363_x_LEU_HD23_Green'],
       ['A_190_x_ALA_N_Blue'],
       ['A_276_x_MET_HE2_Green'],
       ['A_276_x_MET_C_Green'],
       ['A_189_x_PRO_HA_Green'],
       ['A_326_x_CYS_SG_Green'],
       ['A_279_x_LEU_HD23_Green'],
       ['A_290_x_TYR_HB3_Green'],
       ['A_190_x_ALA_N_Blue'],
       ['A_280_x_ILE_O_Red'],
       ['A_276_x_MET_HE2_Green'],
       ['A_290_x_TYR_O_Red'],
       ['A_292_x_ILE_CD1_Green'],
       ['A_324_x_VAL_HG21_Green'],
       ['A_284_x_ASN_ND2_Blue'],
       ['A_324_x_VAL_HG11_Green'],
       ['A_363_x_LEU_CD1_Green'],
       ['A_290_x_TYR_CG_Green'],
       ['A_326_x_CYS_SG_Green'],
       ['A_190_x_ALA_HB2_Green'],
       ['A_367_x_TRP_HH2_Green'],
      

In [30]:
(regular_mesh.get_attribute("vertex_iface")==1).sum()

230

In [31]:
(labels[regular_mesh.get_attribute("vertex_iface")==1]).shape

(230,)

In [14]:
p2_sc_labels[0].sum(axis=1)

array([3.37970894, 2.83356358, 0.        , 1.01809354, 0.6021094 ,
       0.        , 0.        , 3.48175684, 3.43136429, 2.12594253,
       0.        , 0.        , 2.47723065, 4.00300381, 3.27557692,
       0.96478527, 0.41185957, 3.04233171, 1.47229825, 3.17345403,
       0.        , 1.61935911, 0.        , 1.30130604, 2.0102253 ,
       0.        , 3.94578491, 0.92482306, 0.        , 1.98554917,
       2.58657853, 3.68840788, 0.        , 2.09075653, 0.        ,
       1.4487833 , 0.59869715, 3.0009184 , 3.59319065, 2.00282296,
       1.08988893, 1.07576335, 1.05960078, 1.72852172, 1.52048153,
       0.        , 2.82932281, 0.        , 0.        , 2.89680974,
       0.        , 0.        ])

In [ ]:
suf="protein"
ply_file = masif_opts["ply_chain_dir"] + "{}_{}.ply".format(pid,suf)
print(ply_file)

In [257]:
test = np.load("/data/pompei/bw973/Oxygenases/masif/source/test/test.npy")

In [8]:
ALPHA
import os
os.path.basename("data/pompei/bw973/Oxygenases/masif/source/test/test.npy")

'test.npy'

In [6]:
from pymol.cgo import *

obj = []
obj.extend([BEGIN, 0.5])
obj


[2.0, 0.5]

In [256]:
iface3=np.where([(i<2).sum() for i in t2])[0]
regular_names[np.intersect1d(iface3, iface2)]

array(['A_383_x_ARG_CZ_Green', 'A_329_x_TYR_HH_Blue',
       'A_329_x_TYR_CE1_Green', 'A_343_x_LEU_HB3_Green',
       'A_329_x_TYR_CZ_Green', 'A_329_x_TYR_OH_Red',
       'A_329_x_TYR_CE2_Green', 'A_329_x_TYR_CZ_Green',
       'A_329_x_TYR_CG_Green', 'A_343_x_LEU_HD22_Green',
       'A_329_x_TYR_CE1_Green', 'A_383_x_ARG_HH21_Blue',
       'A_383_x_ARG_NE_Blue', 'A_329_x_TYR_HH_Blue',
       'A_383_x_ARG_NH2_Blue', 'A_343_x_LEU_HB2_Green'], dtype='<U22')

In [233]:
regular_names[np.intersect1d(iface3, iface2)]

array(['A_390_x_TYR_CD2_Green', 'A_280_x_ILE_HD11_Green',
       'A_280_x_ILE_CD1_Green', 'A_198_x_ILE_CG2_Green',
       'A_326_x_CYS_HG_Green', 'A_326_x_CYS_SG_Green',
       'A_280_x_ILE_HD11_Green', 'A_276_x_MET_HE1_Green',
       'A_280_x_ILE_HD12_Green', 'A_365_x_PHE_CE2_Green',
       'A_198_x_ILE_CG1_Green', 'A_280_x_ILE_CD1_Green',
       'A_390_x_TYR_CD2_Green'], dtype='<U22')

In [35]:
names=np.concatenate(np.load('data_preparation/01-benchmark_surfaces/Sim_2_traj_42_frame_1367_names.npy',
    allow_pickle=True).item()['names1'])
len(names)

8497

In [2]:
# Header variables and parameters.
import sys
import pymesh
import os
import numpy as np
from IPython.core.debugger import set_trace
import importlib

from scipy.spatial import cKDTree

from default_config.masif_opts import masif_opts

"""
masif_ppi_search_cache_training_data.py: Function to cache all the training data for MaSIF-search. 
                This function extract all the positive pairs and a random number of negative surfaces.
                In the future, the number of negative surfaces should be increased.
Pablo Gainza - LPDI STI EPFL 2019
Released under an Apache License 2.0
"""

params = masif_opts['ppi_search']

custom_params = {}
custom_params['cache_dir'] = 'nn_models/sc05/cache/'
custom_params['model_dir'] = 'nn_models/sc05/all_feat/model_data/'
custom_params['desc_dir'] = 'output/sc05/all_feat/model_data/'
custom_params['gif_eval_out'] = 'nn_models/sc05/gif_eval/'
custom_params['min_sc_filt'] = 0.5
custom_params['max_sc_filt'] = 1.0
custom_params['pos_surf_accept_probability'] = 1.0

for key in custom_params: 
    print('Setting {} to {} '.format(key, custom_params[key]))
    params[key] = custom_params[key]

if 'pids' not in params: 
    params['pids'] = ['p1', 'p2']


# Read the positive first 
parent_in_dir = params['masif_precomputation_dir']

binder_rho_wrt_center = []
binder_theta_wrt_center = []
binder_input_feat = []
binder_mask = []

pos_rho_wrt_center = []
pos_theta_wrt_center = []
pos_input_feat = []
pos_mask = []

neg_rho_wrt_center = []
neg_theta_wrt_center = []
neg_input_feat = []
neg_mask = []

np.random.seed(0)
training_idx = []
val_idx = []
test_idx = []
pos_names = []
neg_names = []

training_list = [x.rstrip() for x in open(params['training_list']).readlines()]
testing_list = [x.rstrip() for x in open(params['testing_list']).readlines()]

idx_count = 0
for count, ppi_pair_id in enumerate(os.listdir(parent_in_dir)[0:10]):
    if ppi_pair_id not in testing_list and ppi_pair_id not in training_list:
        continue
    in_dir = parent_in_dir + ppi_pair_id+'/'
    print(ppi_pair_id)

Setting cache_dir to nn_models/sc05/cache/ 
Setting model_dir to nn_models/sc05/all_feat/model_data/ 
Setting desc_dir to output/sc05/all_feat/model_data/ 
Setting gif_eval_out to nn_models/sc05/gif_eval/ 
Setting min_sc_filt to 0.5 
Setting max_sc_filt to 1.0 
Setting pos_surf_accept_probability to 1.0 
Sim_1_traj_10_frame_10
Sim_1_traj_10_frame_100
Sim_1_traj_10_frame_101
Sim_1_traj_10_frame_1024
Sim_1_traj_10_frame_1025
Sim_1_traj_10_frame_1032
Sim_1_traj_10_frame_1033
Sim_1_traj_10_frame_1034
Sim_1_traj_10_frame_1035
Sim_1_traj_10_frame_1036


In [68]:
ppi_pair_id="Sim_1_traj_42_frame_1246"
in_dir = parent_in_dir + ppi_pair_id+'/'

In [70]:
labels = np.load(in_dir+ppi_pair_id+'_prot_sc_labels.npy')
# Take the median of the percentile 25 shape complementarity.
mylabels = labels[0]
labels = np.median(mylabels, axis=1)
pos_labels = np.where(((labels < -0.2) & (labels > -0.6) | (labels > 0.1)))[0]
K = int(params['pos_surf_accept_probability']*len(pos_labels))
l = np.arange(len(pos_labels))
np.random.shuffle(l)
l = l[:K] 
l = pos_labels[l]

In [73]:
len(pos_labels)
ply_fn1=masif_opts['ply_file_template'].format(ppi_pair_id,"protein")
ply_fn2=masif_opts['ply_file_template'].format(ppi_pair_id,"gas")

In [84]:
m=pymesh.load_mesh(ply_fn1)
m.get_attribute("vertex_iface").sum()


v0 = pymesh.load_mesh(ply_fn1).vertices
v1 = v0[l]
v2 = pymesh.load_mesh(ply_fn2).vertices

In [83]:
import scipy


t2=scipy.spatial.distance_matrix(v0,v2)
names=np.load(masif_opts['ply_chain_dir']+ppi_pair_id+'_names.npy', allow_pickle=True).item()
len(names['names1'])

7386

In [89]:
print(len(names['names1'][m.get_attribute("vertex_iface")==1]))
names['names1'][m.get_attribute("vertex_iface")==2]

181


array([['A_301_x_ALA_CB_Green'],
       ['A_575_x_AKG_CB_Green'],
       ['A_385_x_ALA_C_Green'],
       ['A_252_x_ARG_HH22_Blue'],
       ['A_575_x_AKG_OG2_Red'],
       ['A_575_x_AKG_CD_Green'],
       ['A_327_x_ILE_HG23_Green'],
       ['A_575_x_AKG_CD_Green'],
       ['A_299_x_MET_SD_Green'],
       ['A_386_x_ILE_C_Green'],
       ['A_385_x_ALA_CB_Green'],
       ['A_327_x_ILE_HD13_Green'],
       ['A_301_x_ALA_HB3_Green'],
       ['A_299_x_MET_SD_Green'],
       ['A_252_x_ARG_HH22_Blue'],
       ['A_575_x_AKG_OE1_Red'],
       ['A_575_x_AKG_CA_Green'],
       ['A_301_x_ALA_CB_Green'],
       ['A_387_x_THR_HG22_Green'],
       ['A_327_x_ILE_HD13_Green'],
       ['A_387_x_THR_HG22_Green'],
       ['A_386_x_ILE_N_Blue'],
       ['A_329_x_TYR_CE1_Green'],
       ['A_386_x_ILE_C_Green'],
       ['A_385_x_ALA_HB3_Green'],
       ['A_385_x_ALA_C_Green'],
       ['A_385_x_ALA_O_Red'],
       ['A_575_x_AKG_OE2_Red'],
       ['A_575_x_AKG_CB_Green'],
       ['A_386_x_ILE_C_Green'],
       [

In [86]:
test=[all(i>20) for i in t2]
print(sum(test))
names['names1'][test]

897


array([['A_403_x_TYR_C_Green'],
       ['A_248_x_SER_CB_Green'],
       ['A_574_x_LEU_HD23_Green'],
       ['A_221_x_GLN_CG_Green'],
       ['A_573_x_GLN_HB3_Green'],
       ['A_404_x_LEU_CD2_Green'],
       ['A_217_x_GLU_HB3_Green'],
       ['A_338_x_VAL_CG2_Green'],
       ['A_407_x_GLU_O_Red'],
       ['A_569_x_ASP_O_Red'],
       ['A_400_x_LYS_CE_Green'],
       ['A_402_x_LYS_CD_Green'],
       ['A_405_x_THR_HG23_Green'],
       ['A_561_x_MET_HG2_Green'],
       ['A_265_x_GLY_H_Blue'],
       ['A_574_x_LEU_H_Blue'],
       ['A_405_x_THR_HG1_Blue'],
       ['A_352_x_GLN_NE2_Blue'],
       ['A_403_x_TYR_C_Green'],
       ['A_403_x_TYR_CE2_Green'],
       ['A_573_x_GLN_N_Blue'],
       ['A_400_x_LYS_HB3_Green'],
       ['A_405_x_THR_OG1_Red'],
       ['A_574_x_LEU_C_Green'],
       ['A_351_x_ALA_O_Red'],
       ['A_351_x_ALA_O_Red'],
       ['A_404_x_LEU_HB2_Green'],
       ['A_405_x_THR_CG2_Green'],
       ['A_247_x_SER_C_Green'],
       ['A_403_x_TYR_CZ_Green'],
       ['A_217_x_GLU

In [18]:
# far from oxygen and far from cofactor

In [45]:
len(l)

55

In [28]:
contact_points = np.where(d < params['pos_interface_cutoff'])[0]
l[contact_points]

array([5736, 3873, 4383,  967, 3688, 2652, 6357,  148])

In [38]:
rho_wrt_center = np.load(in_dir+ppi_pair_id+'_rho_wrt_center.npy')
rho_wrt_center.shape

(7266, 50)

In [40]:
kdt = cKDTree(v1)
dneg, rneg = kdt.query(v2)
dneg

array([1.01342249, 1.40968268, 1.06598756, 1.25558481, 1.37221211,
       0.71625719, 1.6384901 , 1.48416606, 1.65418177, 0.82045688,
       0.72294536, 1.37792104, 1.11624431, 1.00061761, 0.90926591,
       0.87982447, 0.30047972, 2.07977642, 2.09082124, 1.00218287,
       1.69207073, 0.88570038, 1.01638686, 1.29595693, 0.95720051,
       0.78258635, 1.31120797, 0.97112744, 1.24211556, 1.91183041,
       1.15465261])

In [43]:
print(len(dneg), len(v1), len(v2))

31 55 31


In [41]:
kdt = cKDTree(v0)
dneg, rneg = kdt.query(v2)
dneg

array([1.01342249, 1.40968268, 1.06598756, 1.25558481, 1.37221211,
       0.71625719, 1.11169442, 1.31744126, 1.52754427, 0.82045688,
       0.72294536, 1.37792104, 1.11624431, 1.00061761, 0.90926591,
       0.87982447, 0.30047972, 1.42236722, 0.87002484, 1.00218287,
       1.69207073, 0.88570038, 1.01638686, 1.29595693, 0.95720051,
       0.78258635, 1.31120797, 0.97112744, 1.24211556, 1.09137259,
       1.15465261])

In [34]:
try:
    kdt = cKDTree(v1)
    dneg, rneg = kdt.query(v2)
except:
    set_trace()
k_neg2 = np.where(dneg > params['pos_interface_cutoff']*2)[0]
k_neg2

array([17, 18])

In [22]:
np.where(d < 2)[0]

array([ 0,  1,  3,  4,  5,  7,  8,  9, 10, 12, 13, 14, 16, 17, 19, 20, 25,
       26, 27, 29, 30, 31, 33, 34, 35, 37, 40, 41, 42, 43, 44, 45, 46, 47,
       49, 51, 52, 53, 54])

In [25]:
kdt.query?

Signature:
kdt.query(
    x,
    k=1,
    eps=0.0,
    p=2.0,
    distance_upper_bound=inf,
    workers=None,
    **kwargs,
)
Docstring:
query(self, x, k=1, eps=0, p=2, distance_upper_bound=np.inf, workers=1)

Query the kd-tree for nearest neighbors

Parameters
----------
x : array_like, last dimension self.m
    An array of points to query.
k : list of integer or integer
    The list of k-th nearest neighbors to return. If k is an
    integer it is treated as a list of [1, ... k] (range(1, k+1)).
    Note that the counting starts from 1.
eps : non-negative float
    Return approximate nearest neighbors; the k-th returned value
    is guaranteed to be no further than (1+eps) times the
    distance to the real k-th nearest neighbor.
p : float, 1<=p<=infinity
    Which Minkowski p-norm to use.
    1 is the sum-of-absolute-values "Manhattan" distance
    2 is the usual Euclidean distance
    infinity is the maximum-coordinate-difference distance
    A finite large p may cause a ValueError

In [12]:
kdt = cKDTree(v2)
d,r= kdt.query(v1)
# Contact points: those within a cutoff distance.
contact_points = np.where(d < params['pos_interface_cutoff'])[0]
try:
    k1 = l[contact_points]
except:
k2 = r[contact_points]

1.0

In [6]:


v1 = pymesh.load_mesh(ply_fn1)
v2 = pymesh.load_mesh(ply_fn2)
# v1 = pymesh.load_mesh(ply_fn1).vertices[l]
# v2 = pymesh.load_mesh(ply_fn2).vertices

In [ ]:
# Read the corresponding ply files. 
fields = ppi_pair_id.split('_')
ply_fn1 = masif_opts['ply_file_template'].format(fields[0], fields[1])
ply_fn2 = masif_opts['ply_file_template'].format(fields[0], fields[2])

In [108]:
regular_names = np.load('data_preparation/01-benchmark_surfaces/Sim_2_traj_42_frame_1410_names.npy',
    allow_pickle=True).item()

regular_mesh=pymesh.load_mesh('data_preparation/01-benchmark_surfaces/Sim_2_traj_42_frame_1410_protein.ply')
regular_mesh.get_attribute("vertex_iface").sum()

full_regular_mesh=pymesh.load_mesh('data_preparation/01-benchmark_surfaces/Sim_2_traj_42_frame_1410_protein_complex.ply')
full_regular_mesh.get_attribute("vertex_iface").sum()
                       

41.0

In [120]:
regular_names['names1'][np.where([(i<4).sum() for i in t2])]

array([['A_211_x_ASP_O_Red'],
       ['A_186_x_LYS_CD_Green'],
       ['A_211_x_ASP_HB2_Green'],
       ['A_209_x_VAL_O_Red'],
       ['A_210_x_VAL_HA_Green'],
       ['A_211_x_ASP_OD2_Red'],
       ['A_211_x_ASP_H_Blue'],
       ['A_211_x_ASP_CB_Green'],
       ['A_197_x_TYR_CG_Green'],
       ['A_209_x_VAL_O_Red'],
       ['A_197_x_TYR_CE2_Green'],
       ['A_188_x_LEU_CD2_Green'],
       ['A_211_x_ASP_O_Red'],
       ['A_210_x_VAL_HA_Green'],
       ['A_197_x_TYR_CZ_Green'],
       ['A_188_x_LEU_HD23_Green'],
       ['A_211_x_ASP_HB3_Green'],
       ['A_188_x_LEU_HB2_Green'],
       ['A_186_x_LYS_HZ3_Blue'],
       ['A_211_x_ASP_OD2_Red'],
       ['A_211_x_ASP_O_Red'],
       ['A_211_x_ASP_HB2_Green'],
       ['A_186_x_LYS_HZ1_Blue'],
       ['A_186_x_LYS_HZ1_Blue'],
       ['A_188_x_LEU_HD21_Green'],
       ['A_209_x_VAL_O_Red'],
       ['A_197_x_TYR_CE2_Green'],
       ['A_211_x_ASP_O_Red'],
       ['A_186_x_LYS_HZ1_Blue'],
       ['A_210_x_VAL_HG13_Green'],
       ['A_197_x_TYR_C

In [90]:
np.where([re.search('A_210',i) for i in regular_names])[0]

array([], dtype=int64)

In [21]:
from sklearn.neighbors import KDTree

kdt = KDTree(v3)
d, r = kdt.query(regular_mesh.vertices)
d = np.square(d)

In [26]:
np.where(d==max(d))

(array([844]), array([0]))

In [35]:
d.max()
np.where(d>=0.5)

(array([ 844, 3515]), array([0, 0]))

In [36]:

test_names['names1'][np.where(d>=0.5)]

array(['A_282_x_HIS_CE1_Green', 'A_191_x_LEU_HD22_Green'], dtype='<U22')

In [405]:
from Bio.PDB import *

function
# Exclude disordered atoms.
class NotDisordered(Select):
    def accept_atom(self, atom):
        return not atom.is_disordered() or atom.get_altloc() == "A"  or atom.get_altloc() == "1" 

tmp_dir= masif_opts['tmp_dir']
out_filename1=out_filename1 = tmp_dir+"/"+pdb
infilename=pdb_filename
outfilename=out_filename1

parser = PDBParser(QUIET=True)
struct = parser.get_structure(infilename, infilename)

model = Selection.unfold_entities(struct, "M")[0]
structBuild = StructureBuilder.StructureBuilder()
structBuild.init_structure("output")
structBuild.init_seg(" ")
structBuild.init_model(0)
outputStruct = structBuild.get_structure()

for chain in model:
    structBuild.init_chain(chain.get_id())
    for residue in chain:
        het = residue.get_id()
        if het[0] == " ":
            outputStruct[0][chain.get_id()].add(residue)
pdbio = PDBIO()
pdbio.set_structure(outputStruct)
pdbio.save(outfilename, select=NotDisordered())

In [353]:
model = Selection.unfold_entities(struct, "M")[0]
structBuild = StructureBuilder.StructureBuilder()
structBuild.init_structure("output")
structBuild.init_seg(" ")
structBuild.init_model(0)
outputStruct = structBuild.get_structure()

for chain in model:
    structBuild.init_chain(chain.get_id())
    for residue in chain:
        het = residue.get_id()
        if het[0] == " ":
            outputStruct[0][chain.get_id()].add(residue)
pdbio = PDBIO()
pdbio.set_structure(outputStruct)
pdbio.save(outfilename, select=NotDisordered())

In [366]:
gases_ligands = ['O2I', 'AKG']
ppdb_df._df['HETATM']

Empty DataFrame
Columns: [record_name, atom_number, blank_1, atom_name, alt_loc, residue_name, blank_2, chain_id, residue_number, insertion, blank_3, x_coord, y_coord, z_coord, occupancy, b_factor, blank_4, segment_id, element_symbol, charge, line_idx]
Index: []

[0 rows x 21 columns]

In [395]:
sel.save(masif_opts["ligand"]["assembly_dir"]+pdb)

In [380]:
sel.save(masif_opts["ligand"]["assembly_dir"]+pdb)
ppdb_df = PandasPdb().read_pdb(masif_opts["ligand"]["assembly_dir"]+pdb)
o2if = ppdb_df.df['ATOM']
o2if[o2if.residue_name.isin(gases_ligands)]

record_name  atom_number blank_1 atom_name alt_loc residue_name blank_2  \
3776        ATOM         3777                CG                  AKG           
3777        ATOM         3778               OG1                  AKG           
3778        ATOM         3779               OG2                  AKG           
3779        ATOM         3780                 C                  AKG           
3780        ATOM         3781                 O                  AKG           
3781        ATOM         3782                CA                  AKG           
3782        ATOM         3783                CB                  AKG           
3783        ATOM         3784                CD                  AKG           
3784        ATOM         3785               OE1                  AKG           
3785        ATOM         3786               OE2                  AKG           
3786        ATOM         3787               HB1                  AKG           
3787        ATOM         3788               HB2                  AKG           
3788        ATOM         3789               HA1                  AKG           
3789        ATOM         3790               HA2                  AKG           
3790        ATOM         3838                OI                  O2I           
3791        ATOM         3839                OI                  O2I           

     chain_id  residue_number insertion  ... x_coord  y_coord  z_coord  \
3776        A             575            ...  40.412   38.074   37.168   
3777        A             575            ...  40.578   39.099   37.880   
3778        A             575            ...  41.293   37.605   36.327   
3779        A             575            ...  39.180   37.256   37.490   
3780        A             575            ...  38.678   37.467   38.643   
3781        A             575            ...  38.362   36.297   36.692   
3782        A             575            ...  36.801   36.165   36.899   
3783        A             575            ...  36.209   35.377   35.823   
3784        A             575            ...  36.812   35.284   34.707   
3785        A             575            ...  35.131   34.799   36.054   
3786        A             575            ...  36.385   37.175   36.774   
3787        A             575            ...  36.480   35.729   37.857   
3788        A             575            ...  38.818   35.312   36.872   
3789        A             575            ...  38.679   36.500   35.658   
3790        A             600            ...  19.665   58.367   26.398   
3791        A             600            ...  18.746   58.878   27.005   

      occupancy  b_factor  blank_4 segment_id element_symbol charge  line_idx  
3776        1.0       0.0                                  C    NaN      3779  
3777        1.0       0.0                                  O    NaN      3780  
3778        1.0       0.0                                  O    NaN      3781  
3779        1.0       0.0                                  C    NaN      3782  
3780        1.0       0.0                                  O    NaN      3783  
3781        1.0       0.0                                  C    NaN      3784  
3782        1.0       0.0                                  C    NaN      3785  
3783        1.0       0.0                                  C    NaN      3786  
3784        1.0       0.0                                  O    NaN      3787  
3785        1.0       0.0                                  O    NaN      3788  
3786        1.0       0.0                                  H    NaN      3789  
3787        1.0       0.0                                  H    NaN      3790  
3788        1.0       0.0                                  H    NaN      3791  
3789        1.0       0.0                                  H    NaN      3792  
3790        1.0       0.0                                  O    NaN      3793  
3791        1.0       0.0                                  O    NaN      3794  

[16 rows x 21 columns]

In [389]:
ppdb_df.df['HETATM']

record_name  atom_number blank_1 atom_name alt_loc residue_name blank_2  \
3776      HETATM         3777                CG                  AKG           
3777      HETATM         3778               OG1                  AKG           
3778      HETATM         3779               OG2                  AKG           
3779      HETATM         3780                 C                  AKG           
3780      HETATM         3781                 O                  AKG           
3781      HETATM         3782                CA                  AKG           
3782      HETATM         3783                CB                  AKG           
3783      HETATM         3784                CD                  AKG           
3784      HETATM         3785               OE1                  AKG           
3785      HETATM         3786               OE2                  AKG           
3786      HETATM         3787               HB1                  AKG           
3787      HETATM         3788               HB2                  AKG           
3788      HETATM         3789               HA1                  AKG           
3789      HETATM         3790               HA2                  AKG           
3790      HETATM         3838                OI                  O2I           
3791      HETATM         3839                OI                  O2I           

     chain_id  residue_number insertion  ... x_coord  y_coord  z_coord  \
3776        A             575            ...  40.412   38.074   37.168   
3777        A             575            ...  40.578   39.099   37.880   
3778        A             575            ...  41.293   37.605   36.327   
3779        A             575            ...  39.180   37.256   37.490   
3780        A             575            ...  38.678   37.467   38.643   
3781        A             575            ...  38.362   36.297   36.692   
3782        A             575            ...  36.801   36.165   36.899   
3783        A             575            ...  36.209   35.377   35.823   
3784        A             575            ...  36.812   35.284   34.707   
3785        A             575            ...  35.131   34.799   36.054   
3786        A             575            ...  36.385   37.175   36.774   
3787        A             575            ...  36.480   35.729   37.857   
3788        A             575            ...  38.818   35.312   36.872   
3789        A             575            ...  38.679   36.500   35.658   
3790        A             600            ...  19.665   58.367   26.398   
3791        A             600            ...  18.746   58.878   27.005   

      occupancy  b_factor  blank_4 segment_id element_symbol charge  line_idx  
3776        1.0       0.0                                  C    NaN      3779  
3777        1.0       0.0                                  O    NaN      3780  
3778        1.0       0.0                                  O    NaN      3781  
3779        1.0       0.0                                  C    NaN      3782  
3780        1.0       0.0                                  O    NaN      3783  
3781        1.0       0.0                                  C    NaN      3784  
3782        1.0       0.0                                  C    NaN      3785  
3783        1.0       0.0                                  C    NaN      3786  
3784        1.0       0.0                                  O    NaN      3787  
3785        1.0       0.0                                  O    NaN      3788  
3786        1.0       0.0                                  H    NaN      3789  
3787        1.0       0.0                                  H    NaN      3790  
3788        1.0       0.0                                  H    NaN      3791  
3789        1.0       0.0                                  H    NaN      3792  
3790        1.0       0.0                                  O    NaN      3793  
3791        1.0       0.0                                  O    NaN      3794  

[16 rows x 21 columns]

In [393]:
ppdb_df._df

{'ATOM':      record_name  atom_number blank_1 atom_name alt_loc residue_name blank_2  \
 0           ATOM            1               CH3                  ACE           
 1           ATOM            2                H1                  ACE           
 2           ATOM            3                H2                  ACE           
 3           ATOM            4                H3                  ACE           
 4           ATOM            5                 C                  ACE           
 ...          ...          ...     ...       ...     ...          ...     ...   
 3771        ATOM         3772              HD23                  LEU           
 3772        ATOM         3773                 C                  LEU           
 3773        ATOM         3774                 O                  LEU           
 3774        ATOM         3775               OXT                  LEU           
 3775        ATOM         3776                H2                  LEU           
 
      chain_id  re

In [396]:
# sel.save(masif_opts["ligand"]["assembly_dir"]+pdb)
         


In [344]:
ppdb_df = PandasPdb().read_pdb(masif_opts["ligand"]["assembly_dir"]+pdb)
o2if = ppdb_df.df['ATOM']
o2if.loc[o2if.residue_name=='O2I','atom_name'] = np.concatenate([['OI1','OI2']] * (len(o2if.loc[o2if.residue_name=='O2I','atom_name'])//2))
ppdb_df._df['ATOM'] = o2if[(o2if['residue_name']!='ACE') & (o2if['residue_name']!='HOH')]
ppdb_df.to_pdb(masif_opts["ligand"]["assembly_dir"]+'/'+pdb)


In [192]:
# which frames have O2IF within 2.5 angstroms of protein or within 9 of AKG
protein = traj.topology.select('protein')
gas2 = traj.topology.select('resname %s' % gas)
AKG = traj.topology.select('resname AKG')


def cmap_per_residue(traj,sel_list,ref_list,cutoff=3.5,metric='euclidean'):
    if len(ref_list)==0 or len(sel_list)==0:
        print("One of the selections is empty")
        return []
    coord1 = traj.xyz[:,sel_list,:]*10.0 # gas
    coord2 = traj.xyz[:,ref_list,:]*10.0 # protein
    residue_sel = np.array([traj.topology.atom(ind).residue.index for ind in sel_list]) # gas
    residue_ref = np.array([traj.topology.atom(ind).residue.index for ind in ref_list])
    residue_sel_un = np.unique(residue_sel) # gas
    residue_ref_un = np.unique(residue_ref)
    dic_sel={t:c  for c,t in enumerate(residue_sel_un)} # gas
    dic_ref={t:c  for c,t in enumerate(residue_ref_un)}
    histo = np.zeros((len(coord1),len(residue_sel_un),len(residue_ref_un)))
    for c,j in enumerate(coord1):
        axis_sel,axis_ref = np.where(scipy.spatial.distance.cdist(coord1[c],coord2[c],metric=metric) < cutoff)
        real_a= residue_sel[axis_sel]
        real_b= residue_ref[axis_ref]
        elements,counts = np.unique(list(zip(real_a,real_b)),axis=0,return_counts=True)
        for c1,el in enumerate(elements):
            ax1=dic_sel[el[0]];
            ax2=dic_ref[el[1]];
            histo[c,ax1,ax2] = counts[c1];
    return residue_sel_un,residue_ref_un,histo




In [199]:
time=np.arange(len(traj))*.01
len(time)

2001

In [200]:
test = cmap_per_residue(traj,gas2,protein,cutoff=2.5)
nfrcond=2

test = cmap_per_residue(traj,gas2,protein,cutoff=2.5)
segments_dict = {}
for i in range(0,24):
    res=test[2][0:,i]
    t=np.zeros(len(traj))
    t[np.where(res)[0]] = 1

    segment=[]
    subsegment,subtime,subframe=[],[],[]
    for c,value in enumerate(t):
        if value==0 and len(subsegment)==0:
            subsegment,subtime=[],[]
        elif value==0 and len(subsegment)!=0:
            if len(subsegment) > nfrcond: 
                segment.append(np.array([subframe,subtime,subsegment]))
            subsegment,subtime,subframe=[],[],[]
        else: 
            subsegment.append(value)
            subtime.append(time[c])
            subframe.append(c)
    if len(subsegment) > nfrcond: segment.append(np.array([subframe,subtime,subsegment]))
    segments_dict[i] = segment

l=[]
for k in segments_dict.keys():
    if len(segments_dict[k]) > 0:
        sl = np.concatenate([r[0] for r in segments_dict[k]])
        l.append(np.unique(sl))
frames = np.unique(np.concatenate(l).astype(int))
fn = frames+1
print(fn)
trajf=traj[frames]

for i,f in enumerate(frames):
    trajfn = trajf[i]
    test2 = cmap_per_residue(trajfn,gas2,protein,cutoff=2.5)
    whr = np.where([j.sum()>0 for j in test2[2][0]])[0]*2
    whr2 = np.concatenate([(n,(n+1)) for n in whr])
    print(whr2)
    atms = np.sort(np.concatenate((gas2[whr2],AKG,protein)))
    sel = trajfn.atom_slice(atms)
    atms = np.sort(np.concatenate((gas2[whr2],AKG,protein)))
    sel = trajfn.atom_slice(atms)
    pdb="Sim_%d_traj_%d_frame_%d" % (simnum, trjnum, f+1)+'.pdb'
    sel.save(masif_opts["ligand"]["assembly_dir"]+pdb)
    
    ppdb_df = PandasPdb().read_pdb(masif_opts["ligand"]["assembly_dir"]+pdb)
    o2if = ppdb_df.df['ATOM']
    o2if.loc[o2if.residue_name=='O2I','atom_name'] = np.concatenate([['OI1','OI2']] * (len(o2if.loc[o2if.residue_name=='O2I','atom_name'])//2))
    ppdb_df._df['ATOM'] = o2if[(o2if['residue_name']!='ACE') & (o2if['residue_name']!='HOH')]
    ppdb_df.to_pdb(masif_opts["ligand"]["assembly_dir"]+'/'+pdb)


[ 439  440  441  445  446  447  461  462  463  473  474  475  493  494
  495  525  526  527  743  744  745 1305 1306 1307 1423 1424 1425 1525
 1526 1527 1593 1594 1595 1788 1789 1790 1791]


In [239]:
for i,f in enumerate(frames):
    trajfn = trajf[i]
    test2 = cmap_per_residue(trajfn,gas2,protein,cutoff=2.5)
    whr = np.where([j.sum()>0 for j in test2[2][0]])[0]*2
    whr2 = np.concatenate([(n,(n+1)) for n in whr])
    print(whr2)
    atms = np.sort(np.concatenate((gas2[whr2],AKG,protein)))
    sel = trajfn.atom_slice(atms)
    atms = np.sort(np.concatenate((gas2[whr2],AKG,protein)))
    sel = trajfn.atom_slice(atms)
    pdb="Sim_%d_traj_%d_frame_%d" % (simnum, trjnum, f+1)+'.pdb'
    sel.save(masif_opts["ligand"]["assembly_dir"]+pdb)
    
    ppdb_df = PandasPdb().read_pdb(masif_opts["ligand"]["assembly_dir"]+pdb)
    o2if = ppdb_df.df['ATOM']
    o2if.loc[o2if.residue_name=='O2I','atom_name'] = np.concatenate([['OI1','OI2']] * (len(o2if.loc[o2if.residue_name=='O2I','atom_name'])//2))
    ppdb_df._df['ATOM'] = o2if[(o2if['residue_name']!='ACE') & (o2if['residue_name']!='HOH')]
    ppdb_df.to_pdb(masif_opts["ligand"]["assembly_dir"]+'/'+pdb)

[4 5]
[4 5]
[4 5]
[34 35]
[ 4  5 34 35]
[ 4  5 34 35]
[34 35]
[34 35]
[34 35]
[34 35]
[34 35]
[34 35]
[34 35]
[34 35]
[34 35]
[34 35]
[34 35]
[34 35]
[24 25]
[24 25]
[24 25]
[12 13 18 19]
[18 19]
[18 19]
[18 19]
[18 19]
[18 19]
[32 33]
[16 17 32 33]
[32 33]
[6 7]
[6 7]
[6 7]
[10 11 14 15]
[10 11]
[10 11 14 15]
[10 11]


In [336]:
df=ppdb_df._df['ATOM']
o2i_uniq = np.unique(df[df.residue_name=='O2I'].residue_number)
o2i_uniq = np.sort(o2i_uniq)

lig_types = []
akg_rn = np.unique(df[df.residue_name=='AKG'].residue_number)
lig_types.append(['AKG','res_%d' % akg_rn])
[lig_types.append([gas, 'res_%d' % i]) for i in o2i_uniq]
np.save(masif_opts["ligand"]["ligand_coords_dir"]+pdb.split('.')[0]+'_ligtypes.npy', lig_types)

lig_coords = {}
lig_coords[akg_rn[0]] = df[df.residue_name=='AKG'][['x_coord', 'y_coord','z_coord']].values
for val in o2i_uniq:
    print(val)
    lig_coords[val] = df[df.residue_number==val][['x_coord', 'y_coord','z_coord']].values

np.save(masif_opts["ligand"]["ligand_coords_dir"]+pdb.split('.')[0]+'_ligcoords.npy', lig_coords)



589


```bash
rm $prefix.pdb
files=$(ls Sim_2*_traj_2*frame**.pdb | sort -V)
prefix=Sim_2_traj_2
for f in $files; do
    echo $(wc -l $f)
    frame=$(echo $f | awk -F_ '{print $NF}' | cut -d. -f1)
    echo "MODEL $frame" >> $prefix.pdb
    cat $f | grep -v MODEL | grep -v 'END$' >> $prefix.pdb
done
echo END >> $prefix.pdb
